## import environment

In [1]:
import pandas as pd
import numpy as np
import re
import string

#NLP lib
import nltk
from nltk.corpus import stopwords
from nltk.corpus import wordnet as wn
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.probability import FreqDist
from textblob import TextBlob
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
from collections import Counter

#Visualization lib
import matplotlib.pyplot as plt 
%matplotlib inline
%pylab
import seaborn as sns
from wordcloud import WordCloud
import cufflinks as cf

import warnings 
warnings.filterwarnings("ignore", category=DeprecationWarning)

Using matplotlib backend: MacOSX
Populating the interactive namespace from numpy and matplotlib


## import data

In [2]:
#import dataset from stakeholders, representative of a category in a city
tw_public = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Taipei/Ko-P/Ko P - tweet.csv')
tw_corpo = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Taipei/Asus/Asus - Tweet.csv')
tw_startup = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Taipei/Gogoro/Gogoro - tweet.csv')
tw_academic = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Taipei/Academia Sinica/Academia Sinica - Tweet.csv')
tw_civil = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Taipei/g0v/g0v - Tweet.csv')
tw_media = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Taipei/Taiwan News/Taiwan News - Tweet.csv')
il_public = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tel Aviv/Ron Huldai/Ron Huldai - Tweet.csv')
il_corpo = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tel Aviv/Check Point Software/Check Point Software - tweet.csv')
il_startup = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tel Aviv/Moovit/Moovit - tweet.csv')
il_academic = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tel Aviv/Tel Aviv University/Tel Aviv University - tweet.csv')
il_civil = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tel Aviv/Hasadna/Hasadna - tweet.csv')
il_media = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tel Aviv/Israel Hayom/Israel Hayom - tweet.csv')
ee_public = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tallinn/Startup Estonia/Startup Estonia - Tweet.csv')
ee_corpo = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tallinn/Bolt/Bolt - Tweet.csv')
ee_startup = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tallinn/AdCash/adCash - Tweet.csv')
ee_academic = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tallinn/TalTech/TalTech - tweet.csv')
ee_civil = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tallinn/CleanTech ForEst/CleanTech ForEst - tweet.csv')
ee_media = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tallinn/Postimees/Postimees - tweet.csv')
taipei = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Taipei/#Taipei.csv')
telaviv = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tel Aviv/#Telaviv.csv')
tallinn = pd.read_csv('/Users/juliencarbonnell/Desktop/Thèse/DONNÉES/1.Twitter/Tallinn/#Tallinn.csv')

In [3]:
#create categorical datasets
all_public = pd.concat([tw_public,il_public,ee_public], axis =0) 
all_corpo = pd.concat([tw_corpo , il_corpo , ee_corpo], axis =0) 
all_startup = pd.concat([tw_startup , il_startup , ee_startup], axis =0) 
all_academic = pd.concat([tw_academic , il_academic , ee_academic], axis =0) 
all_civil = pd.concat([tw_civil , il_civil , ee_civil], axis =0) 
all_media = pd.concat([tw_media , il_media , ee_media], axis =0) 
all_city = pd.concat([taipei , telaviv , tallinn], axis =0)
#create global dataset
global_ = pd.concat([all_public , all_corpo , all_startup , all_academic , all_civil , all_media , all_city], axis =0) 

In [4]:
tw_public.head()

tweet_id city_id            agent_id                twitter_profile  \
0     49185  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
1     49186  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
2     49187  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
3     49188  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
4     49189  Taipei  706869314746327040  https://twitter.com/KP_Taipei   

                                           tweet_url  \
0  https://twitter.com/KP_Taipei/status/120929730...   
1  https://twitter.com/KP_Taipei/status/120894267...   
2  https://twitter.com/KP_Taipei/status/120892310...   
3  https://twitter.com/KP_Taipei/status/120793406...   
4  https://twitter.com/KP_Taipei/status/120757728...   

                                             content total_likes  \
0  On-behalf of the entire City Hall, I wish all ...         141   
1  Very exciting to watch Taipei’s development of...         197   
2  Recently I attended the #AsiaPacificMedicalAca...         134   
3  阿北提醒大家，避免傳染禽流感，早點施打流感疫苗。\n#阿北關心您\n#對抗流感大家一起來 h...         250   
4  It was a great honor to meet with the delegati...         151   

   total_retweet  identified_liker is_reply reply_to initial_tweet  \
0            NaN               NaN      NaN      NaN           NaN   
1            NaN               NaN      NaN      NaN           NaN   
2            NaN               NaN      NaN      NaN           NaN   
3            NaN               NaN      NaN      NaN           NaN   
4            NaN               NaN      NaN      NaN           NaN   

                       tweet_date  
0  Tue Dec 24 02:18:38 +0000 2019  
1  Mon Dec 23 02:49:29 +0000 2019  
2  Mon Dec 23 01:31:42 +0000 2019  
3  Fri Dec 20 08:01:38 +0000 2019  
4  Thu Dec 19 08:23:54 +0000 2019

## delete null values

In [5]:
# how many null values in each content columns ?
print('Ko-P has',tw_public['content'].isna().sum(), 'null tweets')
print('Asus has',tw_corpo['content'].isna().sum(), 'null tweets')
print('Gogoro has',tw_startup['content'].isna().sum(), 'null tweets')
print('Academia Sinica has',tw_academic['content'].isna().sum(), 'null tweets')
print('g0v has',tw_civil['content'].isna().sum(), 'null tweets')
print('Taiwan News has',tw_media['content'].isna().sum(), 'null tweets')
print('Ron Huldai has',il_public['content'].isna().sum(), 'null tweets')
print('Check Point Software has',il_corpo['content'].isna().sum(), 'null tweets')
print('Moovit has',il_startup['content'].isna().sum(), 'null tweets')
print('Tel Aviv University has',il_academic['content'].isna().sum(), 'null tweets')
print('Hasadna has',il_civil['content'].isna().sum(), 'null tweets')
print('Israel Hayom has',il_media['content'].isna().sum(), 'null tweets')
print('Startup Estonia has',ee_public['content'].isna().sum(), 'null tweets')
print('Bolt has',ee_corpo['content'].isna().sum(), 'null tweets')
print('AdCash has',ee_startup['content'].isna().sum(), 'null tweets')
print('Tallinn Tech University has',ee_academic['content'].isna().sum(), 'null tweets')
print('CleanTech ForEst has',ee_civil['content'].isna().sum(), 'null tweets')
print('Postimees has',ee_media['content'].isna().sum(), 'null tweets')
print('#Taipei has',taipei['content'].isna().sum(), 'null tweets')
print('#Telaviv has',telaviv['content'].isna().sum(), 'null tweets')
print('#Tallinn has',tallinn['content'].isna().sum(), 'null tweets')
print('Public Sector category has',all_public['content'].isna().sum(), 'null tweets')
print('Corporate Company category has',all_corpo['content'].isna().sum(), 'null tweets')
print('Startup category has',all_startup['content'].isna().sum(), 'null tweets')
print('Academic Sector category has',all_academic['content'].isna().sum(), 'null tweets')
print('Civil Society category has',all_civil['content'].isna().sum(), 'null tweets')
print('Media category has',all_media['content'].isna().sum(), 'null tweets')
print('Case Study Cities has',all_city['content'].isna().sum(), 'null tweets')
print('In total there are',global_['content'].isna().sum(), 'null tweets')

Ko-P has 126 null tweets
Asus has 1323 null tweets
Gogoro has 1096 null tweets
Academia Sinica has 175 null tweets
g0v has 164 null tweets
Taiwan News has 1423 null tweets
Ron Huldai has 81 null tweets
Check Point Software has 4833 null tweets
Moovit has 4856 null tweets
Tel Aviv University has 3738 null tweets
Hasadna has 248 null tweets
Israel Hayom has 30 null tweets
Startup Estonia has 2061 null tweets
Bolt has 1503 null tweets
AdCash has 226 null tweets
Tallinn Tech University has 124 null tweets
CleanTech ForEst has 230 null tweets
Postimees has 0 null tweets
#Taipei has 0 null tweets
#Telaviv has 4 null tweets
#Tallinn has 0 null tweets
Public Sector category has 2268 null tweets
Corporate Company category has 7659 null tweets
Startup category has 6178 null tweets
Academic Sector category has 4037 null tweets
Civil Society category has 642 null tweets
Media category has 1453 null tweets
Case Study Cities has 4 null tweets
In total there are 22241 null tweets


In [6]:
# keep only rows when content column value is not null
tw_public = tw_public[tw_public['content'].notnull()]
tw_corpo = tw_corpo[tw_corpo['content'].notnull()]
tw_startup = tw_startup[tw_startup['content'].notnull()]
tw_academic = tw_academic[tw_academic['content'].notnull()]
tw_civil = tw_civil[tw_civil['content'].notnull()]
tw_media = tw_media[tw_media['content'].notnull()]
il_public = il_public[il_public['content'].notnull()]
il_corpo = il_corpo[il_corpo['content'].notnull()]
il_startup = il_startup[il_startup['content'].notnull()]
il_academic = il_academic[il_academic['content'].notnull()]
il_civil = il_civil[il_civil['content'].notnull()]
il_media = il_media[il_media['content'].notnull()]
ee_public = ee_public[ee_public['content'].notnull()]
ee_corpo = ee_corpo[ee_corpo['content'].notnull()]
ee_startup = ee_startup[ee_startup['content'].notnull()]
ee_academic = ee_academic[ee_academic['content'].notnull()]
ee_civil = ee_civil[ee_civil['content'].notnull()]
ee_media = ee_media[ee_media['content'].notnull()]
taipei = taipei[taipei['content'].notnull()]
telaviv = telaviv[telaviv['content'].notnull()]
tallinn = tallinn[tallinn['content'].notnull()]
all_public = all_public[all_public['content'].notnull()]
all_corpo = all_corpo[all_corpo['content'].notnull()]
all_startup = all_startup[all_startup['content'].notnull()]
all_academic = all_academic[all_academic['content'].notnull()]
all_civil = all_civil[all_civil['content'].notnull()]
all_media = all_media[all_media['content'].notnull()]
all_city = all_city[all_city['content'].notnull()]
global_ = global_[global_['content'].notnull()]

In [7]:
# check null values again
print('Ko-P has',tw_public['content'].isna().sum(), 'null tweets')
print('Asus has',tw_corpo['content'].isna().sum(), 'null tweets')
print('Gogoro has',tw_startup['content'].isna().sum(), 'null tweets')
print('Academia Sinica has',tw_academic['content'].isna().sum(), 'null tweets')
print('g0v has',tw_civil['content'].isna().sum(), 'null tweets')
print('Taiwan News has',tw_media['content'].isna().sum(), 'null tweets')
print('Ron Huldai has',il_public['content'].isna().sum(), 'null tweets')
print('Check Point Software has',il_corpo['content'].isna().sum(), 'null tweets')
print('Moovit has',il_startup['content'].isna().sum(), 'null tweets')
print('Tel Aviv University has',il_academic['content'].isna().sum(), 'null tweets')
print('Hasadna has',il_civil['content'].isna().sum(), 'null tweets')
print('Israel Hayom has',il_media['content'].isna().sum(), 'null tweets')
print('Startup Estonia has',ee_public['content'].isna().sum(), 'null tweets')
print('Bolt has',ee_corpo['content'].isna().sum(), 'null tweets')
print('AdCash has',ee_startup['content'].isna().sum(), 'null tweets')
print('Tallinn Tech University has',ee_academic['content'].isna().sum(), 'null tweets')
print('CleanTech ForEst has',ee_civil['content'].isna().sum(), 'null tweets')
print('Postimees has',ee_media['content'].isna().sum(), 'null tweets')
print('#Taipei has',taipei['content'].isna().sum(), 'null tweets')
print('#Telaviv has',telaviv['content'].isna().sum(), 'null tweets')
print('#Tallinn has',tallinn['content'].isna().sum(), 'null tweets')
print('Public Sector category has',all_public['content'].isna().sum(), 'null tweets')
print('Corporate Company category has',all_corpo['content'].isna().sum(), 'null tweets')
print('Startup category has',all_startup['content'].isna().sum(), 'null tweets')
print('Academic Sector category has',all_academic['content'].isna().sum(), 'null tweets')
print('Civil Society category has',all_civil['content'].isna().sum(), 'null tweets')
print('Media category has',all_media['content'].isna().sum(), 'null tweets')
print('Case Study Cities has',all_city['content'].isna().sum(), 'null tweets')
print('In total there are',global_['content'].isna().sum(), 'null tweets')

Ko-P has 0 null tweets
Asus has 0 null tweets
Gogoro has 0 null tweets
Academia Sinica has 0 null tweets
g0v has 0 null tweets
Taiwan News has 0 null tweets
Ron Huldai has 0 null tweets
Check Point Software has 0 null tweets
Moovit has 0 null tweets
Tel Aviv University has 0 null tweets
Hasadna has 0 null tweets
Israel Hayom has 0 null tweets
Startup Estonia has 0 null tweets
Bolt has 0 null tweets
AdCash has 0 null tweets
Tallinn Tech University has 0 null tweets
CleanTech ForEst has 0 null tweets
Postimees has 0 null tweets
#Taipei has 0 null tweets
#Telaviv has 0 null tweets
#Tallinn has 0 null tweets
Public Sector category has 0 null tweets
Corporate Company category has 0 null tweets
Startup category has 0 null tweets
Academic Sector category has 0 null tweets
Civil Society category has 0 null tweets
Media category has 0 null tweets
Case Study Cities has 0 null tweets
In total there are 0 null tweets


In [8]:
#how many values in each dataset ?
print('Ko-P has',tw_public['content'].count(), ' tweets')
print('Asus has',tw_corpo['content'].count(), ' tweets')
print('Gogoro has',tw_startup['content'].count(), ' tweets')
print('Academia Sinica has',tw_academic['content'].count(), ' tweets')
print('g0v has',tw_civil['content'].count(), ' tweets')
print('Taiwan News has',tw_media['content'].count(), ' tweets')
print('Ron Huldai has',il_public['content'].count(), ' tweets')
print('Check Point Software has',il_corpo['content'].count(), ' tweets')
print('Moovit has',il_startup['content'].count(), ' tweets')
print('Tel Aviv University has',il_academic['content'].count(), ' tweets')
print('Hasadna has',il_civil['content'].count(), ' tweets')
print('Israel Hayom has',il_media['content'].count(), ' tweets')
print('Startup Estonia has',ee_public['content'].count(), ' tweets')
print('Bolt has',ee_corpo['content'].count(), ' tweets')
print('AdCash has',ee_startup['content'].count(), ' tweets')
print('Tallinn Tech University has',ee_academic['content'].count(), ' tweets')
print('CleanTech ForEst has',ee_civil['content'].count(), ' tweets')
print('Postimees has',ee_media['content'].count(), ' tweets')
print('#Taipei has',taipei['content'].count(), ' tweets')
print('#Telaviv has',telaviv['content'].count(), ' tweets')
print('#Tallinn has',tallinn['content'].count(), ' tweets')
print('Public Sector category has',all_public['content'].count(), ' tweets')
print('Corporate Company category has',all_corpo['content'].count(), ' tweets')
print('Startup category has',all_startup['content'].count(), ' tweets')
print('Academic Sector category has',all_academic['content'].count(), ' tweets')
print('Civil Society category has',all_civil['content'].count(), ' tweets')
print('Media category has',all_media['content'].count(), ' tweets')
print('Case Study Cities has',all_city['content'].count(), ' tweets')
print('In total there are',global_['content'].count(), ' tweets')

Ko-P has 1274  tweets
Asus has 3639  tweets
Gogoro has 988  tweets
Academia Sinica has 376  tweets
g0v has 156  tweets
Taiwan News has 3223  tweets
Ron Huldai has 707  tweets
Check Point Software has 3790  tweets
Moovit has 3658  tweets
Tel Aviv University has 3311  tweets
Hasadna has 2171  tweets
Israel Hayom has 2877  tweets
Startup Estonia has 3410  tweets
Bolt has 2540  tweets
AdCash has 846  tweets
Tallinn Tech University has 637  tweets
CleanTech ForEst has 469  tweets
Postimees has 3229  tweets
#Taipei has 17341  tweets
#Telaviv has 17620  tweets
#Tallinn has 6299  tweets
Public Sector category has 5391  tweets
Corporate Company category has 9969  tweets
Startup category has 5492  tweets
Academic Sector category has 4324  tweets
Civil Society category has 2796  tweets
Media category has 9329  tweets
Case Study Cities has 41260  tweets
In total there are 78561  tweets


In [9]:
# calculate the sum of total_likes for each dataset

# count  non null values of the total_likes column
print('Ko-P has',tw_public['total_likes'].notnull().sum(), 'liked tweets')
print('Asus has',tw_corpo['total_likes'].notnull().sum(), 'liked tweets')
print('Gogoro has',tw_startup['total_likes'].notnull().sum(), 'liked tweets')
print('Academia Sinica has',tw_academic['total_likes'].notnull().sum(), 'liked tweets')
print('g0v has',tw_civil['total_likes'].notnull().sum(), 'liked tweets')
print('Taiwan News has',tw_media['total_likes'].notnull().sum(), 'liked tweets')
print('Ron Huldai has',il_public['total_likes'].notnull().sum(), 'liked tweets')
print('Check Point Software has',il_corpo['total_likes'].notnull().sum(), 'liked tweets')
print('Moovit has',il_startup['total_likes'].notnull().sum(), 'liked tweets')
print('Tel Aviv University has',il_academic['total_likes'].notnull().sum(), 'liked tweets')
print('Hasadna has',il_civil['total_likes'].notnull().sum(), 'liked tweets')
print('Israel Hayom has',il_media['total_likes'].notnull().sum(), 'liked tweets')
print('Startup Estonia has',ee_public['total_likes'].notnull().sum(), 'liked tweets')
print('Bolt has',ee_corpo['total_likes'].notnull().sum(), 'liked tweets')
print('AdCash has',ee_startup['total_likes'].notnull().sum(), 'liked tweets')
print('Tallinn Tech University has',ee_academic['total_likes'].notnull().sum(), 'liked tweets')
print('CleanTech ForEst has',ee_civil['total_likes'].notnull().sum(), 'liked tweets')
print('Postimees has',ee_media['total_likes'].notnull().sum(), 'liked tweets')
print('Public Sector category has',all_public['total_likes'].notnull().sum(), 'liked tweets')
print('Corporate Company category has',all_corpo['total_likes'].notnull().sum(), 'liked tweets')
print('Startup category has',all_startup['total_likes'].notnull().sum(), 'liked tweets')
print('Academic Sector category has',all_academic['total_likes'].notnull().sum(), 'liked tweets')
print('Civil Society category has',all_civil['total_likes'].notnull().sum(), 'liked tweets')
print('Media category has',all_media['total_likes'].notnull().sum(), 'liked tweets')
print('In total there are',global_['total_likes'].notnull().sum(), 'liked tweets')

Ko-P has 191 liked tweets
Asus has 2947 liked tweets
Gogoro has 294 liked tweets
Academia Sinica has 293 liked tweets
g0v has 151 liked tweets
Taiwan News has 0 liked tweets
Ron Huldai has 233 liked tweets
Check Point Software has 673 liked tweets
Moovit has 667 liked tweets
Tel Aviv University has 596 liked tweets
Hasadna has 459 liked tweets
Israel Hayom has 418 liked tweets
Startup Estonia has 451 liked tweets
Bolt has 71 liked tweets
AdCash has 317 liked tweets
Tallinn Tech University has 290 liked tweets
CleanTech ForEst has 337 liked tweets
Postimees has 166 liked tweets
Public Sector category has 875 liked tweets
Corporate Company category has 3691 liked tweets
Startup category has 1278 liked tweets
Academic Sector category has 1179 liked tweets
Civil Society category has 947 liked tweets
Media category has 584 liked tweets
In total there are 8554 liked tweets


In [10]:
# calculate the mean and standard dev of total_likes
print('Ko-P has',tw_public['total_likes'].notnull().sum(), 'likes')
print('Asus has',tw_corpo['total_likes'].notnull().sum(), 'likes')
print('Gogoro has',tw_startup['total_likes'].notnull().sum(), 'likes')
print('Academia Sinica has',tw_academic['total_likes'].notnull().sum(), 'likes')
print('g0v has',tw_civil['total_likes'].notnull().sum(), 'likes')
print('Taiwan News has',tw_media['total_likes'].notnull().sum(), 'likes')
print('Ron Huldai has',il_public['total_likes'].notnull().sum(), 'likes')
print('Check Point Software has',il_corpo['total_likes'].notnull().sum(), 'likes')
print('Moovit has',il_startup['total_likes'].notnull().sum(), 'likes')
print('Tel Aviv University has',il_academic['total_likes'].notnull().sum(), 'likes')
print('Hasadna has',il_civil['total_likes'].notnull().sum(), 'likes')
print('Israel Hayom has',il_media['total_likes'].notnull().sum(), 'likes')
print('Startup Estonia has',ee_public['total_likes'].notnull().sum(), 'likes')
print('Bolt has',ee_corpo['total_likes'].notnull().sum(), 'likes')
print('AdCash has',ee_startup['total_likes'].notnull().sum(), 'likes')
print('Tallinn Tech University has',ee_academic['total_likes'].notnull().sum(), 'likes')
print('CleanTech ForEst has',ee_civil['total_likes'].notnull().sum(), 'likes')
print('Postimees has',ee_media['total_likes'].notnull().sum(), 'likes')
print('Public Sector category has',all_public['total_likes'].notnull().sum(), 'likes')
print('Corporate Company category has',all_corpo['total_likes'].notnull().sum(), 'likes')
print('Startup category has',all_startup['total_likes'].notnull().sum(), 'likes')
print('Academic Sector category has',all_academic['total_likes'].notnull().sum(), 'likes')
print('Civil Society category has',all_civil['total_likes'].notnull().sum(), 'likes')
print('Media category has',all_media['total_likes'].notnull().sum(), 'likes')
print('In total there are',global_['total_likes'].notnull().sum(), 'likes')

Ko-P has 191 likes
Asus has 2947 likes
Gogoro has 294 likes
Academia Sinica has 293 likes
g0v has 151 likes
Taiwan News has 0 likes
Ron Huldai has 233 likes
Check Point Software has 673 likes
Moovit has 667 likes
Tel Aviv University has 596 likes
Hasadna has 459 likes
Israel Hayom has 418 likes
Startup Estonia has 451 likes
Bolt has 71 likes
AdCash has 317 likes
Tallinn Tech University has 290 likes
CleanTech ForEst has 337 likes
Postimees has 166 likes
Public Sector category has 875 likes
Corporate Company category has 3691 likes
Startup category has 1278 likes
Academic Sector category has 1179 likes
Civil Society category has 947 likes
Media category has 584 likes
In total there are 8554 likes


## Perform sentiment analysis

In [11]:
# create a new column with sentiment analysis polarity based on content
tw_public['polarity'] = tw_public['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
tw_corpo['polarity'] = tw_corpo['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
tw_startup['polarity'] = tw_startup['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
tw_academic['polarity'] = tw_academic['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
tw_civil['polarity'] = tw_civil['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
tw_media['polarity'] = tw_media['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
il_public['polarity'] = il_public['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
il_corpo['polarity'] = il_corpo['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
il_startup['polarity'] = il_startup['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
il_academic['polarity'] = il_academic['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
il_civil['polarity'] = il_civil['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
il_media['polarity'] = il_media['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
ee_public['polarity'] = ee_public['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
ee_corpo['polarity'] = ee_corpo['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
ee_startup['polarity'] = ee_startup['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
ee_academic['polarity'] = ee_academic['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
ee_civil['polarity'] = ee_civil['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
ee_media['polarity'] = ee_media['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
taipei['polarity'] = taipei['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
telaviv['polarity'] = telaviv['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
tallinn['polarity'] = tallinn['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
all_public['polarity'] = all_public['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
all_corpo['polarity'] = all_corpo['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
all_startup['polarity'] = all_startup['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
all_academic['polarity'] = all_academic['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
all_civil['polarity'] = all_civil['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
all_media['polarity'] = all_media['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
all_city['polarity'] = all_city['content'].apply(lambda x: TextBlob(x).sentiment.polarity)
global_['polarity'] = global_['content'].apply(lambda x: TextBlob(x).sentiment.polarity)

tw_public['subjectivity'] = tw_public['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
tw_corpo['subjectivity'] = tw_corpo['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
tw_startup['subjectivity'] = tw_startup['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
tw_academic['subjectivity'] = tw_academic['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
tw_civil['subjectivity'] = tw_civil['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
tw_media['subjectivity'] = tw_media['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
il_public['subjectivity'] = il_public['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
il_corpo['subjectivity'] = il_corpo['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
il_startup['subjectivity'] = il_startup['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
il_academic['subjectivity'] = il_academic['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
il_civil['subjectivity'] = il_civil['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
il_media['subjectivity'] = il_media['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
ee_public['subjectivity'] = ee_public['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
ee_corpo['subjectivity'] = ee_corpo['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
ee_startup['subjectivity'] = ee_startup['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
ee_academic['subjectivity'] = ee_academic['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
ee_civil['subjectivity'] = ee_civil['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
ee_media['subjectivity'] = ee_media['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
taipei['subjectivity'] = taipei['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
telaviv['subjectivity'] = telaviv['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
tallinn['subjectivity'] = tallinn['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
all_public['subjectivity'] = all_public['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
all_corpo['subjectivity'] = all_corpo['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
all_startup['subjectivity'] = all_startup['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
all_academic['subjectivity'] = all_academic['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
all_civil['subjectivity'] = all_civil['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
all_media['subjectivity'] = all_media['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
all_city['subjectivity'] = all_city['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)
global_['subjectivity'] = global_['content'].apply(lambda x: TextBlob(x).sentiment.subjectivity)

In [12]:
# calculare means and standard devs for each new columns
print('tw_public polarity mean', ("%.2f" % (np.mean(tw_public['polarity']))))
print('tw_public subjectivity mean', ("%.2f" % (np.mean(tw_public['subjectivity']))))
print('tw_corpo polarity mean', ("%.2f" % (np.mean(tw_corpo['polarity']))))
print('tw_corpo subjectivity mean', ("%.2f" % (np.mean(tw_corpo['subjectivity']))))
print('tw_startup polarity mean', ("%.2f" % (np.mean(tw_startup['polarity']))))
print('tw_startup subjectivity mean', ("%.2f" % (np.mean(tw_startup['subjectivity']))))
print('tw_academic polarity mean', ("%.2f" % (np.mean(tw_academic['polarity']))))
print('tw_academic subjectivity mean', ("%.2f" % (np.mean(tw_academic['subjectivity']))))
print('tw_civil polarity mean', ("%.2f" % (np.mean(tw_civil['polarity']))))
print('tw_civil subjectivity mean', ("%.2f" % (np.mean(tw_civil['subjectivity']))))
print('tw_media polarity mean', ("%.2f" % (np.mean(tw_media['polarity']))))
print('tw_media subjectivity mean', ("%.2f" % (np.mean(tw_media['subjectivity']))))
print('il_public polarity mean', ("%.2f" % (np.mean(il_public['polarity']))))
print('il_public subjectivity mean', ("%.2f" % (np.mean(il_public['subjectivity']))))
print('il_corpo polarity mean', ("%.2f" % (np.mean(il_corpo['polarity']))))
print('il_corpo subjectivity mean', ("%.2f" % (np.mean(il_corpo['subjectivity']))))
print('il_startup polarity mean', ("%.2f" % (np.mean(il_startup['polarity']))))
print('il_startup subjectivity mean', ("%.2f" % (np.mean(il_startup['subjectivity']))))
print('il_academic polarity mean', ("%.2f" % (np.mean(il_academic['polarity']))))
print('il_academic subjectivity mean', ("%.2f" % (np.mean(il_academic['subjectivity']))))
print('il_civil polarity mean', ("%.2f" % (np.mean(il_civil['polarity']))))
print('il_civil subjectivity mean', ("%.2f" % (np.mean(il_civil['subjectivity']))))
print('il_media polarity mean', ("%.2f" % (np.mean(il_media['polarity']))))
print('il_media subjectivity mean', ("%.2f" % (np.mean(il_media['subjectivity']))))
print('ee_public polarity mean', ("%.2f" % (np.mean(ee_public['polarity']))))
print('ee_public subjectivity mean', ("%.2f" % (np.mean(ee_public['subjectivity']))))
print('ee_corpo polarity mean', ("%.2f" % (np.mean(ee_corpo['polarity']))))
print('ee_corpo subjectivity mean', ("%.2f" % (np.mean(ee_corpo['subjectivity']))))
print('ee_startup polarity mean', ("%.2f" % (np.mean(ee_startup['polarity']))))
print('ee_startup subjectivity mean', ("%.2f" % (np.mean(ee_startup['subjectivity']))))
print('ee_academic polarity mean', ("%.2f" % (np.mean(ee_academic['polarity']))))
print('ee_academic subjectivity mean', ("%.2f" % (np.mean(ee_academic['subjectivity']))))
print('ee_civil polarity mean', ("%.2f" % (np.mean(ee_civil['polarity']))))
print('ee_civil subjectivity mean', ("%.2f" % (np.mean(ee_civil['subjectivity']))))
print('ee_media polarity mean', ("%.2f" % (np.mean(ee_media['polarity']))))
print('ee_media subjectivity mean', ("%.2f" % (np.mean(ee_media['subjectivity']))))
print('taipei polarity mean', ("%.2f" % (np.mean(taipei['polarity']))))
print('taipei subjectivity mean', ("%.2f" % (np.mean(taipei['subjectivity']))))
print('telaviv polarity mean', ("%.2f" % (np.mean(telaviv['polarity']))))
print('telaviv subjectivity mean', ("%.2f" % (np.mean(telaviv['subjectivity']))))
print('tallinn polarity mean', ("%.2f" % (np.mean(tallinn['polarity']))))
print('tallinn subjectivity mean', ("%.2f" % (np.mean(tallinn['subjectivity']))))
print('all_public polarity mean', ("%.2f" % (np.mean(all_public['polarity']))))
print('all_public subjectivity mean', ("%.2f" % (np.mean(all_public['subjectivity']))))
print('all_corpo polarity mean', ("%.2f" % (np.mean(all_corpo['polarity']))))
print('all_corpo subjectivity mean', ("%.2f" % (np.mean(all_corpo['subjectivity']))))
print('all_startup polarity mean', ("%.2f" % (np.mean(all_startup['polarity']))))
print('all_startup subjectivity mean', ("%.2f" % (np.mean(all_startup['subjectivity']))))
print('all_academic polarity mean', ("%.2f" % (np.mean(all_academic['polarity']))))
print('all_academic subjectivity mean', ("%.2f" % (np.mean(all_academic['subjectivity']))))
print('all_civil polarity mean', ("%.2f" % (np.mean(all_civil['polarity']))))
print('all_civil subjectivity mean', ("%.2f" % (np.mean(all_civil['subjectivity']))))
print('all_media polarity mean', ("%.2f" % (np.mean(all_media['polarity']))))
print('all_media subjectivity mean', ("%.2f" % (np.mean(all_media['subjectivity']))))
print('all_city polarity mean', ("%.2f" % (np.mean(all_city['polarity']))))
print('all_city subjectivity mean', ("%.2f" % (np.mean(all_city['subjectivity']))))
print('global polarity mean', ("%.2f" % (np.mean(global_['polarity']))))
print('global subjectivity mean', ("%.2f" % (np.mean(global_['subjectivity']))))

tw_public polarity mean 0.15
tw_public subjectivity mean 0.29
tw_corpo polarity mean 0.27
tw_corpo subjectivity mean 0.46
tw_startup polarity mean 0.16
tw_startup subjectivity mean 0.32
tw_academic polarity mean 0.17
tw_academic subjectivity mean 0.32
tw_civil polarity mean 0.14
tw_civil subjectivity mean 0.33
tw_media polarity mean 0.03
tw_media subjectivity mean 0.19
il_public polarity mean 0.02
il_public subjectivity mean 0.02
il_corpo polarity mean 0.18
il_corpo subjectivity mean 0.38
il_startup polarity mean 0.21
il_startup subjectivity mean 0.38
il_academic polarity mean 0.18
il_academic subjectivity mean 0.31
il_civil polarity mean 0.04
il_civil subjectivity mean 0.10
il_media polarity mean 0.05
il_media subjectivity mean 0.26
ee_public polarity mean 0.18
ee_public subjectivity mean 0.30
ee_corpo polarity mean 0.10
ee_corpo subjectivity mean 0.41
ee_startup polarity mean 0.21
ee_startup subjectivity mean 0.38
ee_academic polarity mean 0.17
ee_academic subjectivity mean 0.25
ee_c

In [13]:
print('tw_public polarity std', ("%.2f" % (np.std(tw_public['polarity']))))
print('tw_public subjectivity std', ("%.2f" % (np.std(tw_public['subjectivity']))))
print('tw_corpo polarity std', ("%.2f" % (np.std(tw_corpo['polarity']))))
print('tw_corpo subjectivity std', ("%.2f" % (np.std(tw_corpo['subjectivity']))))
print('tw_startup polarity std', ("%.2f" % (np.std(tw_startup['polarity']))))
print('tw_startup subjectivity std', ("%.2f" % (np.std(tw_startup['subjectivity']))))
print('tw_academic polarity std', ("%.2f" % (np.std(tw_academic['polarity']))))
print('tw_academic subjectivity std', ("%.2f" % (np.std(tw_academic['subjectivity']))))
print('tw_civil polarity std', ("%.2f" % (np.std(tw_civil['polarity']))))
print('tw_civil subjectivity std', ("%.2f" % (np.std(tw_civil['subjectivity']))))
print('tw_media polarity std', ("%.2f" % (np.std(tw_media['polarity']))))
print('tw_media subjectivity std', ("%.2f" % (np.std(tw_media['subjectivity']))))
print('il_public polarity std', ("%.2f" % (np.std(il_public['polarity']))))
print('il_public subjectivity std', ("%.2f" % (np.std(il_public['subjectivity']))))
print('il_corpo polarity std', ("%.2f" % (np.std(il_corpo['polarity']))))
print('il_corpo subjectivity std', ("%.2f" % (np.std(il_corpo['subjectivity']))))
print('il_startup polarity std', ("%.2f" % (np.std(il_startup['polarity']))))
print('il_startup subjectivity std', ("%.2f" % (np.std(il_startup['subjectivity']))))
print('il_academic polarity std', ("%.2f" % (np.std(il_academic['polarity']))))
print('il_academic subjectivity std', ("%.2f" % (np.std(il_academic['subjectivity']))))
print('il_civil polarity std', ("%.2f" % (np.std(il_civil['polarity']))))
print('il_civil subjectivity std', ("%.2f" % (np.std(il_civil['subjectivity']))))
print('il_media polarity std', ("%.2f" % (np.std(il_media['polarity']))))
print('il_media subjectivity std', ("%.2f" % (np.std(il_media['subjectivity']))))
print('ee_public polarity std', ("%.2f" % (np.std(ee_public['polarity']))))
print('ee_public subjectivity std', ("%.2f" % (np.std(ee_public['subjectivity']))))
print('ee_corpo polarity std', ("%.2f" % (np.std(ee_corpo['polarity']))))
print('ee_corpo subjectivity std', ("%.2f" % (np.std(ee_corpo['subjectivity']))))
print('ee_startup polarity std', ("%.2f" % (np.std(ee_startup['polarity']))))
print('ee_startup subjectivity std', ("%.2f" % (np.std(ee_startup['subjectivity']))))
print('ee_academic polarity std', ("%.2f" % (np.std(ee_academic['polarity']))))
print('ee_academic subjectivity std', ("%.2f" % (np.std(ee_academic['subjectivity']))))
print('ee_civil polarity std', ("%.2f" % (np.std(ee_civil['polarity']))))
print('ee_civil subjectivity std', ("%.2f" % (np.std(ee_civil['subjectivity']))))
print('ee_media polarity std', ("%.2f" % (np.std(ee_media['polarity']))))
print('ee_media subjectivity mestdan', ("%.2f" % (np.std(ee_media['subjectivity']))))
print('taipei polarity std', ("%.2f" % (np.std(taipei['polarity']))))
print('taipei subjectivity std', ("%.2f" % (np.std(taipei['subjectivity']))))
print('telaviv polarity std', ("%.2f" % (np.std(telaviv['polarity']))))
print('telaviv subjectivity std', ("%.2f" % (np.std(telaviv['subjectivity']))))
print('tallinn polarity std', ("%.2f" % (np.std(tallinn['polarity']))))
print('tallinn subjectivity std', ("%.2f" % (np.std(tallinn['subjectivity']))))
print('all_public polarity std', ("%.2f" % (np.std(all_public['polarity']))))
print('all_public subjectivity std', ("%.2f" % (np.std(all_public['subjectivity']))))
print('all_corpo polarity std', ("%.2f" % (np.std(all_corpo['polarity']))))
print('all_corpo subjectivity std', ("%.2f" % (np.std(all_corpo['subjectivity']))))
print('all_startup polarity std', ("%.2f" % (np.std(all_startup['polarity']))))
print('all_startup subjectivity std', ("%.2f" % (np.std(all_startup['subjectivity']))))
print('all_academic polarity std', ("%.2f" % (np.std(all_academic['polarity']))))
print('all_academic subjectivity std', ("%.2f" % (np.std(all_academic['subjectivity']))))
print('all_civil polarity std', ("%.2f" % (np.std(all_civil['polarity']))))
print('all_civil subjectivity std', ("%.2f" % (np.std(all_civil['subjectivity']))))
print('all_media polarity std', ("%.2f" % (np.std(all_media['polarity']))))
print('all_media subjectivity std', ("%.2f" % (np.std(all_media['subjectivity']))))
print('all_city polarity std', ("%.2f" % (np.std(all_city['polarity']))))
print('all_city subjectivity std', ("%.2f" % (np.std(all_city['subjectivity']))))
print('global polarity std', ("%.2f" % (np.std(global_['polarity']))))
print('global subjectivity std', ("%.2f" % (np.std(global_['subjectivity']))))

tw_public polarity std 0.24
tw_public subjectivity std 0.31
tw_corpo polarity std 0.31
tw_corpo subjectivity std 0.33
tw_startup polarity std 0.27
tw_startup subjectivity std 0.31
tw_academic polarity std 0.29
tw_academic subjectivity std 0.32
tw_civil polarity std 0.24
tw_civil subjectivity std 0.32
tw_media polarity std 0.18
tw_media subjectivity std 0.27
il_public polarity std 0.12
il_public subjectivity std 0.14
il_corpo polarity std 0.27
il_corpo subjectivity std 0.30
il_startup polarity std 0.27
il_startup subjectivity std 0.32
il_academic polarity std 0.29
il_academic subjectivity std 0.32
il_civil polarity std 0.16
il_civil subjectivity std 0.24
il_media polarity std 0.24
il_media subjectivity std 0.31
ee_public polarity std 0.29
ee_public subjectivity std 0.32
ee_corpo polarity std 0.31
ee_corpo subjectivity std 0.35
ee_startup polarity std 0.27
ee_startup subjectivity std 0.30
ee_academic polarity std 0.27
ee_academic subjectivity std 0.30
ee_civil polarity std 0.26
ee_civil 

In [14]:
# use vader sentiment to get % of pos, neg, neu
analyzer= SentimentIntensityAnalyzer()
#{'neg': 0.0, 'neu': 0.494, 'pos': 0.506, 'compound': 0.6249}

#Add VADER metrics to dataframe
tw_public['compound'] = [analyzer.polarity_scores(v)['compound'] for v in tw_public['content']]
tw_public['neg'] = [analyzer.polarity_scores(v)['neg'] for v in tw_public['content']]
tw_public['neu'] = [analyzer.polarity_scores(v)['neu'] for v in tw_public['content']]
tw_public['pos'] = [analyzer.polarity_scores(v)['pos'] for v in tw_public['content']]
tw_corpo['compound'] = [analyzer.polarity_scores(v)['compound'] for v in tw_corpo['content']]
tw_corpo['neg'] = [analyzer.polarity_scores(v)['neg'] for v in tw_corpo['content']]
tw_corpo['neu'] = [analyzer.polarity_scores(v)['neu'] for v in tw_corpo['content']]
tw_corpo['pos'] = [analyzer.polarity_scores(v)['pos'] for v in tw_corpo['content']]
tw_startup['compound'] = [analyzer.polarity_scores(v)['compound'] for v in tw_startup['content']]
tw_startup['neg'] = [analyzer.polarity_scores(v)['neg'] for v in tw_startup['content']]
tw_startup['neu'] = [analyzer.polarity_scores(v)['neu'] for v in tw_startup['content']]
tw_startup['pos'] = [analyzer.polarity_scores(v)['pos'] for v in tw_startup['content']]
tw_academic['compound'] = [analyzer.polarity_scores(v)['compound'] for v in tw_academic['content']]
tw_academic['neg'] = [analyzer.polarity_scores(v)['neg'] for v in tw_academic['content']]
tw_academic['neu'] = [analyzer.polarity_scores(v)['neu'] for v in tw_academic['content']]
tw_academic['pos'] = [analyzer.polarity_scores(v)['pos'] for v in tw_academic['content']]
tw_civil['compound'] = [analyzer.polarity_scores(v)['compound'] for v in tw_civil['content']]
tw_civil['neg'] = [analyzer.polarity_scores(v)['neg'] for v in tw_civil['content']]
tw_civil['neu'] = [analyzer.polarity_scores(v)['neu'] for v in tw_civil['content']]
tw_civil['pos'] = [analyzer.polarity_scores(v)['pos'] for v in tw_civil['content']]
tw_media['compound'] = [analyzer.polarity_scores(v)['compound'] for v in tw_media['content']]
tw_media['neg'] = [analyzer.polarity_scores(v)['neg'] for v in tw_media['content']]
tw_media['neu'] = [analyzer.polarity_scores(v)['neu'] for v in tw_media['content']]
tw_media['pos'] = [analyzer.polarity_scores(v)['pos'] for v in tw_media['content']]
il_public['compound'] = [analyzer.polarity_scores(v)['compound'] for v in il_public['content']]
il_public['neg'] = [analyzer.polarity_scores(v)['neg'] for v in il_public['content']]
il_public['neu'] = [analyzer.polarity_scores(v)['neu'] for v in il_public['content']]
il_public['pos'] = [analyzer.polarity_scores(v)['pos'] for v in il_public['content']]
il_corpo['compound'] = [analyzer.polarity_scores(v)['compound'] for v in il_corpo['content']]
il_corpo['neg'] = [analyzer.polarity_scores(v)['neg'] for v in il_corpo['content']]
il_corpo['neu'] = [analyzer.polarity_scores(v)['neu'] for v in il_corpo['content']]
il_corpo['pos'] = [analyzer.polarity_scores(v)['pos'] for v in il_corpo['content']]
il_startup['compound'] = [analyzer.polarity_scores(v)['compound'] for v in il_startup['content']]
il_startup['neg'] = [analyzer.polarity_scores(v)['neg'] for v in il_startup['content']]
il_startup['neu'] = [analyzer.polarity_scores(v)['neu'] for v in il_startup['content']]
il_startup['pos'] = [analyzer.polarity_scores(v)['pos'] for v in il_startup['content']]
il_academic['compound'] = [analyzer.polarity_scores(v)['compound'] for v in il_academic['content']]
il_academic['neg'] = [analyzer.polarity_scores(v)['neg'] for v in il_academic['content']]
il_academic['neu'] = [analyzer.polarity_scores(v)['neu'] for v in il_academic['content']]
il_academic['pos'] = [analyzer.polarity_scores(v)['pos'] for v in il_academic['content']]
il_civil['compound'] = [analyzer.polarity_scores(v)['compound'] for v in il_civil['content']]
il_civil['neg'] = [analyzer.polarity_scores(v)['neg'] for v in il_civil['content']]
il_civil['neu'] = [analyzer.polarity_scores(v)['neu'] for v in il_civil['content']]
il_civil['pos'] = [analyzer.polarity_scores(v)['pos'] for v in il_civil['content']]
il_media['compound'] = [analyzer.polarity_scores(v)['compound'] for v in il_media['content']]
il_media['neg'] = [analyzer.polarity_scores(v)['neg'] for v in il_media['content']]
il_media['neu'] = [analyzer.polarity_scores(v)['neu'] for v in il_media['content']]
il_media['pos'] = [analyzer.polarity_scores(v)['pos'] for v in il_media['content']]
ee_public['compound'] = [analyzer.polarity_scores(v)['compound'] for v in ee_public['content']]
ee_public['neg'] = [analyzer.polarity_scores(v)['neg'] for v in ee_public['content']]
ee_public['neu'] = [analyzer.polarity_scores(v)['neu'] for v in ee_public['content']]
ee_public['pos'] = [analyzer.polarity_scores(v)['pos'] for v in ee_public['content']]
ee_corpo['compound'] = [analyzer.polarity_scores(v)['compound'] for v in ee_corpo['content']]
ee_corpo['neg'] = [analyzer.polarity_scores(v)['neg'] for v in ee_corpo['content']]
ee_corpo['neu'] = [analyzer.polarity_scores(v)['neu'] for v in ee_corpo['content']]
ee_corpo['pos'] = [analyzer.polarity_scores(v)['pos'] for v in ee_corpo['content']]
ee_startup['compound'] = [analyzer.polarity_scores(v)['compound'] for v in ee_startup['content']]
ee_startup['neg'] = [analyzer.polarity_scores(v)['neg'] for v in ee_startup['content']]
ee_startup['neu'] = [analyzer.polarity_scores(v)['neu'] for v in ee_startup['content']]
ee_startup['pos'] = [analyzer.polarity_scores(v)['pos'] for v in ee_startup['content']]
ee_academic['compound'] = [analyzer.polarity_scores(v)['compound'] for v in ee_academic['content']]
ee_academic['neg'] = [analyzer.polarity_scores(v)['neg'] for v in ee_academic['content']]
ee_academic['neu'] = [analyzer.polarity_scores(v)['neu'] for v in ee_academic['content']]
ee_academic['pos'] = [analyzer.polarity_scores(v)['pos'] for v in ee_academic['content']]
ee_civil['compound'] = [analyzer.polarity_scores(v)['compound'] for v in ee_civil['content']]
ee_civil['neg'] = [analyzer.polarity_scores(v)['neg'] for v in ee_civil['content']]
ee_civil['neu'] = [analyzer.polarity_scores(v)['neu'] for v in ee_civil['content']]
ee_civil['pos'] = [analyzer.polarity_scores(v)['pos'] for v in ee_civil['content']]
ee_media['compound'] = [analyzer.polarity_scores(v)['compound'] for v in ee_media['content']]
ee_media['neg'] = [analyzer.polarity_scores(v)['neg'] for v in ee_media['content']]
ee_media['neu'] = [analyzer.polarity_scores(v)['neu'] for v in ee_media['content']]
ee_media['pos'] = [analyzer.polarity_scores(v)['pos'] for v in ee_media['content']]
taipei['compound'] = [analyzer.polarity_scores(v)['compound'] for v in taipei['content']]
taipei['neg'] = [analyzer.polarity_scores(v)['neg'] for v in taipei['content']]
taipei['neu'] = [analyzer.polarity_scores(v)['neu'] for v in taipei['content']]
taipei['pos'] = [analyzer.polarity_scores(v)['pos'] for v in taipei['content']]
telaviv['compound'] = [analyzer.polarity_scores(v)['compound'] for v in telaviv['content']]
telaviv['neg'] = [analyzer.polarity_scores(v)['neg'] for v in telaviv['content']]
telaviv['neu'] = [analyzer.polarity_scores(v)['neu'] for v in telaviv['content']]
telaviv['pos'] = [analyzer.polarity_scores(v)['pos'] for v in telaviv['content']]
tallinn['compound'] = [analyzer.polarity_scores(v)['compound'] for v in tallinn['content']]
tallinn['neg'] = [analyzer.polarity_scores(v)['neg'] for v in tallinn['content']]
tallinn['neu'] = [analyzer.polarity_scores(v)['neu'] for v in tallinn['content']]
tallinn['pos'] = [analyzer.polarity_scores(v)['pos'] for v in tallinn['content']]
all_public['compound'] = [analyzer.polarity_scores(v)['compound'] for v in all_public['content']]
all_public['neg'] = [analyzer.polarity_scores(v)['neg'] for v in all_public['content']]
all_public['neu'] = [analyzer.polarity_scores(v)['neu'] for v in all_public['content']]
all_public['pos'] = [analyzer.polarity_scores(v)['pos'] for v in all_public['content']]
all_corpo['compound'] = [analyzer.polarity_scores(v)['compound'] for v in all_corpo['content']]
all_corpo['neg'] = [analyzer.polarity_scores(v)['neg'] for v in all_corpo['content']]
all_corpo['neu'] = [analyzer.polarity_scores(v)['neu'] for v in all_corpo['content']]
all_corpo['pos'] = [analyzer.polarity_scores(v)['pos'] for v in all_corpo['content']]
all_startup['compound'] = [analyzer.polarity_scores(v)['compound'] for v in all_startup['content']]
all_startup['neg'] = [analyzer.polarity_scores(v)['neg'] for v in all_startup['content']]
all_startup['neu'] = [analyzer.polarity_scores(v)['neu'] for v in all_startup['content']]
all_startup['pos'] = [analyzer.polarity_scores(v)['pos'] for v in all_startup['content']]
all_academic['compound'] = [analyzer.polarity_scores(v)['compound'] for v in all_academic['content']]
all_academic['neg'] = [analyzer.polarity_scores(v)['neg'] for v in all_academic['content']]
all_academic['neu'] = [analyzer.polarity_scores(v)['neu'] for v in all_academic['content']]
all_academic['pos'] = [analyzer.polarity_scores(v)['pos'] for v in all_academic['content']]
all_civil['compound'] = [analyzer.polarity_scores(v)['compound'] for v in all_civil['content']]
all_civil['neg'] = [analyzer.polarity_scores(v)['neg'] for v in all_civil['content']]
all_civil['neu'] = [analyzer.polarity_scores(v)['neu'] for v in all_civil['content']]
all_civil['pos'] = [analyzer.polarity_scores(v)['pos'] for v in all_civil['content']]
all_media['compound'] = [analyzer.polarity_scores(v)['compound'] for v in all_media['content']]
all_media['neg'] = [analyzer.polarity_scores(v)['neg'] for v in all_media['content']]
all_media['neu'] = [analyzer.polarity_scores(v)['neu'] for v in all_media['content']]
all_media['pos'] = [analyzer.polarity_scores(v)['pos'] for v in all_media['content']]
all_city['compound'] = [analyzer.polarity_scores(v)['compound'] for v in all_city['content']]
all_city['neg'] = [analyzer.polarity_scores(v)['neg'] for v in all_city['content']]
all_city['neu'] = [analyzer.polarity_scores(v)['neu'] for v in all_city['content']]
all_city['pos'] = [analyzer.polarity_scores(v)['pos'] for v in all_city['content']]
global_['compound'] = [analyzer.polarity_scores(v)['compound'] for v in global_['content']]
global_['neg'] = [analyzer.polarity_scores(v)['neg'] for v in global_['content']]
global_['neu'] = [analyzer.polarity_scores(v)['neu'] for v in global_['content']]
global_['pos'] = [analyzer.polarity_scores(v)['pos'] for v in global_['content']]

In [15]:
#calculare means and standard devs for each new column
print('tw_public negative mean', ("%.2f" % (np.mean(tw_public['neg']))))
print('tw_public neutral mean', ("%.2f" % (np.mean(tw_public['neu']))))
print('tw_public positive mean', ("%.2f" % (np.mean(tw_public['pos']))))
print('tw_corpo negative mean', ("%.2f" % (np.mean(tw_corpo['neg']))))
print('tw_corpo neutral mean', ("%.2f" % (np.mean(tw_corpo['neu']))))
print('tw_corpo positive mean', ("%.2f" % (np.mean(tw_corpo['pos']))))
print('tw_startup negative mean', ("%.2f" % (np.mean(tw_startup['neg']))))
print('tw_startup neutral mean', ("%.2f" % (np.mean(tw_startup['neu']))))
print('tw_startup positive mean', ("%.2f" % (np.mean(tw_startup['pos']))))
print('tw_academic negative mean', ("%.2f" % (np.mean(tw_academic['neg']))))
print('tw_academic neutral mean', ("%.2f" % (np.mean(tw_academic['neu']))))
print('tw_academic positive mean', ("%.2f" % (np.mean(tw_academic['pos']))))
print('tw_civil negative mean', ("%.2f" % (np.mean(tw_civil['neg']))))
print('tw_civil neutral mean', ("%.2f" % (np.mean(tw_civil['neu']))))
print('tw_civil positive mean', ("%.2f" % (np.mean(tw_civil['pos']))))
print('tw_media negative mean', ("%.2f" % (np.mean(tw_media['neg']))))
print('tw_media neutral mean', ("%.2f" % (np.mean(tw_media['neu']))))
print('tw_media positive mean', ("%.2f" % (np.mean(tw_media['pos']))))
print('il_public negative mean', ("%.2f" % (np.mean(il_public['neg']))))
print('il_public neutral mean', ("%.2f" % (np.mean(il_public['neu']))))
print('il_public positive mean', ("%.2f" % (np.mean(il_public['pos']))))
print('il_corpo negative mean', ("%.2f" % (np.mean(il_corpo['neg']))))
print('il_corpo neutral mean', ("%.2f" % (np.mean(il_corpo['neu']))))
print('il_corpo positive mean', ("%.2f" % (np.mean(il_corpo['pos']))))
print('il_startup negative mean', ("%.2f" % (np.mean(il_startup['neg']))))
print('il_startup neutral mean', ("%.2f" % (np.mean(il_startup['neu']))))
print('il_startup positive mean', ("%.2f" % (np.mean(il_startup['pos']))))
print('il_academic negative mean', ("%.2f" % (np.mean(il_academic['neg']))))
print('il_academic neutral mean', ("%.2f" % (np.mean(il_academic['neu']))))
print('il_academic positive mean', ("%.2f" % (np.mean(il_academic['pos']))))
print('il_civil negative mean', ("%.2f" % (np.mean(il_civil['neg']))))
print('il_civil neutral mean', ("%.2f" % (np.mean(il_civil['neu']))))
print('il_civil positive mean', ("%.2f" % (np.mean(il_civil['pos']))))
print('il_media negative mean', ("%.2f" % (np.mean(il_media['neg']))))
print('il_media neutral mean', ("%.2f" % (np.mean(il_media['neu']))))
print('il_media positive mean', ("%.2f" % (np.mean(il_media['pos']))))
print('ee_public negative mean', ("%.2f" % (np.mean(ee_public['neg']))))
print('ee_public neutral mean', ("%.2f" % (np.mean(ee_public['neu']))))
print('ee_public positive mean', ("%.2f" % (np.mean(ee_public['pos']))))
print('ee_corpo negative mean', ("%.2f" % (np.mean(ee_corpo['neg']))))
print('ee_corpo neutral mean', ("%.2f" % (np.mean(ee_corpo['neu']))))
print('ee_corpo positive mean', ("%.2f" % (np.mean(ee_corpo['pos']))))
print('ee_startup negative mean', ("%.2f" % (np.mean(ee_startup['neg']))))
print('ee_startup neutral mean', ("%.2f" % (np.mean(ee_startup['neu']))))
print('ee_startup positive mean', ("%.2f" % (np.mean(ee_startup['pos']))))
print('ee_academic negative mean', ("%.2f" % (np.mean(ee_academic['neg']))))
print('ee_academic neutral mean', ("%.2f" % (np.mean(ee_academic['neu']))))
print('ee_academic positive mean', ("%.2f" % (np.mean(ee_academic['pos']))))
print('ee_civil negative mean', ("%.2f" % (np.mean(ee_civil['neg']))))
print('ee_civil neutral mean', ("%.2f" % (np.mean(ee_civil['neu']))))
print('ee_civil positive mean', ("%.2f" % (np.mean(ee_civil['pos']))))
print('ee_media negative mean', ("%.2f" % (np.mean(ee_media['neg']))))
print('ee_media neutral mean', ("%.2f" % (np.mean(ee_media['neu']))))
print('ee_media positive mean', ("%.2f" % (np.mean(ee_media['pos']))))
print('taipei negative mean', ("%.2f" % (np.mean(taipei['neg']))))
print('taipei neutral mean', ("%.2f" % (np.mean(taipei['neu']))))
print('taipei positive mean', ("%.2f" % (np.mean(taipei['pos']))))
print('telaviv negative mean', ("%.2f" % (np.mean(telaviv['neg']))))
print('telaviv neutral mean', ("%.2f" % (np.mean(telaviv['neu']))))
print('telaviv positive mean', ("%.2f" % (np.mean(telaviv['pos']))))
print('tallinn negative mean', ("%.2f" % (np.mean(tallinn['neg']))))
print('tallinn neutral mean', ("%.2f" % (np.mean(tallinn['neu']))))
print('tallinn positive mean', ("%.2f" % (np.mean(tallinn['pos']))))
print('all_public negative mean', ("%.2f" % (np.mean(all_public['neg']))))
print('all_public neutral mean', ("%.2f" % (np.mean(all_public['neu']))))
print('all_public positive mean', ("%.2f" % (np.mean(all_public['pos']))))
print('all_corpo negative mean', ("%.2f" % (np.mean(all_corpo['neg']))))
print('all_corpo neutral mean', ("%.2f" % (np.mean(all_corpo['neu']))))
print('all_corpo positive mean', ("%.2f" % (np.mean(all_corpo['pos']))))
print('all_startup negative mean', ("%.2f" % (np.mean(all_startup['neg']))))
print('all_startup neutral mean', ("%.2f" % (np.mean(all_startup['neu']))))
print('all_startup positive mean', ("%.2f" % (np.mean(all_startup['pos']))))
print('all_academic negative mean', ("%.2f" % (np.mean(all_academic['neg']))))
print('all_academic neutral mean', ("%.2f" % (np.mean(all_academic['neu']))))
print('all_academic positive mean', ("%.2f" % (np.mean(all_academic['pos']))))
print('all_civil negative mean', ("%.2f" % (np.mean(all_civil['neg']))))
print('all_civil neutral mean', ("%.2f" % (np.mean(all_civil['neu']))))
print('all_civil positive mean', ("%.2f" % (np.mean(all_civil['pos']))))
print('all_media negative mean', ("%.2f" % (np.mean(all_media['neg']))))
print('all_media neutral mean', ("%.2f" % (np.mean(all_media['neu']))))
print('all_media positive mean', ("%.2f" % (np.mean(all_media['pos']))))
print('all_city negative mean', ("%.2f" % (np.mean(all_city['neg']))))
print('all_city neutral mean', ("%.2f" % (np.mean(all_city['neu']))))
print('all_city positive mean', ("%.2f" % (np.mean(all_city['pos']))))
print('global negative mean', ("%.2f" % (np.mean(global_['neg']))))
print('global neutral mean', ("%.2f" % (np.mean(global_['neu']))))
print('global positive mean', ("%.2f" % (np.mean(global_['pos']))))

print('tw_public negative std', ("%.2f" % (np.std(tw_public['neg']))))
print('tw_public neutral std', ("%.2f" % (np.std(tw_public['neu']))))
print('tw_public positive std', ("%.2f" % (np.std(tw_public['pos']))))
print('tw_corpo negative std', ("%.2f" % (np.std(tw_corpo['neg']))))
print('tw_corpo neutral std', ("%.2f" % (np.std(tw_corpo['neu']))))
print('tw_corpo positive std', ("%.2f" % (np.std(tw_corpo['pos']))))
print('tw_startup negative std', ("%.2f" % (np.std(tw_startup['neg']))))
print('tw_startup neutral std', ("%.2f" % (np.std(tw_startup['neu']))))
print('tw_startup positive std', ("%.2f" % (np.std(tw_startup['pos']))))
print('tw_academic negative std', ("%.2f" % (np.std(tw_academic['neg']))))
print('tw_academic neutral std', ("%.2f" % (np.std(tw_academic['neu']))))
print('tw_academic positive std', ("%.2f" % (np.std(tw_academic['pos']))))
print('tw_civil negative std', ("%.2f" % (np.std(tw_civil['neg']))))
print('tw_civil neutral std', ("%.2f" % (np.std(tw_civil['neu']))))
print('tw_civil positive std', ("%.2f" % (np.std(tw_civil['pos']))))
print('tw_media negative std', ("%.2f" % (np.std(tw_media['neg']))))
print('tw_media neutral std', ("%.2f" % (np.std(tw_media['neu']))))
print('tw_media positive std', ("%.2f" % (np.std(tw_media['pos']))))
print('il_public negative std', ("%.2f" % (np.std(il_public['neg']))))
print('il_public neutral std', ("%.2f" % (np.std(il_public['neu']))))
print('il_public positive std', ("%.2f" % (np.std(il_public['pos']))))
print('il_corpo negative std', ("%.2f" % (np.std(il_corpo['neg']))))
print('il_corpo neutral std', ("%.2f" % (np.std(il_corpo['neu']))))
print('il_corpo positive std', ("%.2f" % (np.std(il_corpo['pos']))))
print('il_startup negative std', ("%.2f" % (np.std(il_startup['neg']))))
print('il_startup neutral std', ("%.2f" % (np.std(il_startup['neu']))))
print('il_startup positive std', ("%.2f" % (np.std(il_startup['pos']))))
print('il_academic negative std', ("%.2f" % (np.std(il_academic['neg']))))
print('il_academic neutral std', ("%.2f" % (np.std(il_academic['neu']))))
print('il_academic positive std', ("%.2f" % (np.std(il_academic['pos']))))
print('il_civil negative std', ("%.2f" % (np.std(il_civil['neg']))))
print('il_civil neutral std', ("%.2f" % (np.std(il_civil['neu']))))
print('il_civil positive std', ("%.2f" % (np.std(il_civil['pos']))))
print('il_media negative std', ("%.2f" % (np.std(il_media['neg']))))
print('il_media neutral std', ("%.2f" % (np.std(il_media['neu']))))
print('il_media positive std', ("%.2f" % (np.std(il_media['pos']))))
print('ee_public negative std', ("%.2f" % (np.std(ee_public['neg']))))
print('ee_public neutral std', ("%.2f" % (np.std(ee_public['neu']))))
print('ee_public positive std', ("%.2f" % (np.std(ee_public['pos']))))
print('ee_corpo negative std', ("%.2f" % (np.std(ee_corpo['neg']))))
print('ee_corpo neutral std', ("%.2f" % (np.std(ee_corpo['neu']))))
print('ee_corpo positive std', ("%.2f" % (np.std(ee_corpo['pos']))))
print('ee_startup negative std', ("%.2f" % (np.std(ee_startup['neg']))))
print('ee_startup neutral std', ("%.2f" % (np.std(ee_startup['neu']))))
print('ee_startup positive std', ("%.2f" % (np.std(ee_startup['pos']))))
print('ee_academic negative std', ("%.2f" % (np.std(ee_academic['neg']))))
print('ee_academic neutral std', ("%.2f" % (np.std(ee_academic['neu']))))
print('ee_academic positive std', ("%.2f" % (np.std(ee_academic['pos']))))
print('ee_civil negative std', ("%.2f" % (np.std(ee_civil['neg']))))
print('ee_civil neutral std', ("%.2f" % (np.std(ee_civil['neu']))))
print('ee_civil positive std', ("%.2f" % (np.std(ee_civil['pos']))))
print('ee_media negative std', ("%.2f" % (np.std(ee_media['neg']))))
print('ee_media neutral std', ("%.2f" % (np.std(ee_media['neu']))))
print('ee_media positive std', ("%.2f" % (np.std(ee_media['pos']))))
print('taipei negative std', ("%.2f" % (np.std(taipei['neg']))))
print('taipei neutral std', ("%.2f" % (np.std(taipei['neu']))))
print('taipei positive std', ("%.2f" % (np.std(taipei['pos']))))
print('telaviv negative std', ("%.2f" % (np.std(telaviv['neg']))))
print('telaviv neutral std', ("%.2f" % (np.std(telaviv['neu']))))
print('telaviv positive std', ("%.2f" % (np.std(telaviv['pos']))))
print('tallinn negative std', ("%.2f" % (np.std(tallinn['neg']))))
print('tallinn neutral std', ("%.2f" % (np.std(tallinn['neu']))))
print('tallinn positive std', ("%.2f" % (np.std(tallinn['pos']))))
print('all_public negative std', ("%.2f" % (np.std(all_public['neg']))))
print('all_public neutral std', ("%.2f" % (np.std(all_public['neu']))))
print('all_public positive std', ("%.2f" % (np.std(all_public['pos']))))
print('all_corpo negative std', ("%.2f" % (np.std(all_corpo['neg']))))
print('all_corpo neutral std', ("%.2f" % (np.std(all_corpo['neu']))))
print('all_corpo positive std', ("%.2f" % (np.std(all_corpo['pos']))))
print('all_startup negative std', ("%.2f" % (np.std(all_startup['neg']))))
print('all_startup neutral std', ("%.2f" % (np.std(all_startup['neu']))))
print('all_startup positive std', ("%.2f" % (np.std(all_startup['pos']))))
print('all_academic negative std', ("%.2f" % (np.std(all_academic['neg']))))
print('all_academic neutral std', ("%.2f" % (np.std(all_academic['neu']))))
print('all_academic positive std', ("%.2f" % (np.std(all_academic['pos']))))
print('all_civil negative std', ("%.2f" % (np.std(all_civil['neg']))))
print('all_civil neutral std', ("%.2f" % (np.std(all_civil['neu']))))
print('all_civil positive std', ("%.2f" % (np.std(all_civil['pos']))))
print('all_media negative std', ("%.2f" % (np.std(all_media['neg']))))
print('all_media neutral std', ("%.2f" % (np.std(all_media['neu']))))
print('all_media positive std', ("%.2f" % (np.std(all_media['pos']))))
print('all_city negative std', ("%.2f" % (np.std(all_city['neg']))))
print('all_city neutral std', ("%.2f" % (np.std(all_city['neu']))))
print('all_city positive std', ("%.2f" % (np.std(all_city['pos']))))
print('global negative std', ("%.2f" % (np.std(global_['neg']))))
print('global neutral std', ("%.2f" % (np.std(global_['neu']))))
print('global positive std', ("%.2f" % (np.std(global_['pos']))))

tw_public negative mean 0.01
tw_public neutral mean 0.87
tw_public positive mean 0.13
tw_corpo negative mean 0.02
tw_corpo neutral mean 0.81
tw_corpo positive mean 0.17
tw_startup negative mean 0.02
tw_startup neutral mean 0.83
tw_startup positive mean 0.15
tw_academic negative mean 0.02
tw_academic neutral mean 0.86
tw_academic positive mean 0.12
tw_civil negative mean 0.01
tw_civil neutral mean 0.90
tw_civil positive mean 0.09
tw_media negative mean 0.06
tw_media neutral mean 0.87
tw_media positive mean 0.07
il_public negative mean 0.00
il_public neutral mean 0.99
il_public positive mean 0.00
il_corpo negative mean 0.05
il_corpo neutral mean 0.82
il_corpo positive mean 0.13
il_startup negative mean 0.02
il_startup neutral mean 0.81
il_startup positive mean 0.18
il_academic negative mean 0.02
il_academic neutral mean 0.85
il_academic positive mean 0.13
il_civil negative mean 0.01
il_civil neutral mean 0.96
il_civil positive mean 0.03
il_media negative mean 0.09
il_media neutral mean 0

## extract features from datasets

In [16]:
#add a column with content length for each tweet
tw_public['content_len'] = tw_public['content'].apply(lambda x: len(x))
tw_corpo['content_len'] = tw_corpo['content'].apply(lambda x: len(x))
tw_startup['content_len'] = tw_startup['content'].apply(lambda x: len(x))
tw_academic['content_len'] = tw_academic['content'].apply(lambda x: len(x))
tw_civil['content_len'] = tw_civil['content'].apply(lambda x: len(x))
tw_media['content_len'] = tw_media['content'].apply(lambda x: len(x))
il_public['content_len'] = il_public['content'].apply(lambda x: len(x))
il_corpo['content_len'] = il_corpo['content'].apply(lambda x: len(x))
il_startup['content_len'] = il_startup['content'].apply(lambda x: len(x))
il_academic['content_len'] = il_academic['content'].apply(lambda x: len(x))
il_civil['content_len'] = il_civil['content'].apply(lambda x: len(x))
il_media['content_len'] = il_media['content'].apply(lambda x: len(x))
ee_public['content_len'] = ee_public['content'].apply(lambda x: len(x))
ee_corpo['content_len'] = ee_corpo['content'].apply(lambda x: len(x))
ee_startup['content_len'] = ee_startup['content'].apply(lambda x: len(x))
ee_academic['content_len'] = ee_academic['content'].apply(lambda x: len(x))
ee_civil['content_len'] = ee_civil['content'].apply(lambda x: len(x))
ee_media['content_len'] = ee_media['content'].apply(lambda x: len(x))
taipei['content_len'] = taipei['content'].apply(lambda x: len(x))
telaviv['content_len'] = telaviv['content'].apply(lambda x: len(x))
tallinn['content_len'] = tallinn['content'].apply(lambda x: len(x))
all_public['content_len'] = all_public['content'].apply(lambda x: len(x))
all_corpo['content_len'] = all_corpo['content'].apply(lambda x: len(x))
all_startup['content_len'] = all_startup['content'].apply(lambda x: len(x))
all_academic['content_len'] = all_academic['content'].apply(lambda x: len(x))
all_civil['content_len'] = all_civil['content'].apply(lambda x: len(x))
all_media['content_len'] = all_media['content'].apply(lambda x: len(x))
all_city['content_len'] = all_city['content'].apply(lambda x: len(x))
global_['content_len'] = global_['content'].apply(lambda x: len(x))

In [17]:
#calculare means and standard devs for each new columns
print('tw_public tweet length mean', ("%.2f" % (np.mean(tw_public['content_len']))))
print('tw_corpo tweet length mean', ("%.2f" % (np.mean(tw_corpo['content_len']))))
print('tw_startup tweet length mean', ("%.2f" % (np.mean(tw_startup['content_len']))))
print('tw_academic tweet length mean', ("%.2f" % (np.mean(tw_academic['content_len']))))
print('tw_civil tweet length mean', ("%.2f" % (np.mean(tw_civil['content_len']))))
print('tw_media tweet length mean', ("%.2f" % (np.mean(tw_media['content_len']))))
print('il_public tweet length mean', ("%.2f" % (np.mean(il_public['content_len']))))
print('il_corpo tweet length mean', ("%.2f" % (np.mean(il_corpo['content_len']))))
print('il_startup tweet length mean', ("%.2f" % (np.mean(il_startup['content_len']))))
print('il_academic tweet length mean', ("%.2f" % (np.mean(il_academic['content_len']))))
print('il_civil tweet length mean', ("%.2f" % (np.mean(il_civil['content_len']))))
print('il_media tweet length mean', ("%.2f" % (np.mean(il_media['content_len']))))
print('ee_public tweet length mean', ("%.2f" % (np.mean(ee_public['content_len']))))
print('ee_corpo tweet length mean', ("%.2f" % (np.mean(ee_corpo['content_len']))))
print('ee_startup tweet length mean', ("%.2f" % (np.mean(ee_startup['content_len']))))
print('ee_academic tweet length mean', ("%.2f" % (np.mean(ee_academic['content_len']))))
print('ee_civil tweet length mean', ("%.2f" % (np.mean(ee_civil['content_len']))))
print('ee_media tweet length mean', ("%.2f" % (np.mean(ee_media['content_len']))))
print('taipei tweet length mean', ("%.2f" % (np.mean(taipei['content_len']))))
print('telaviv tweet length mean', ("%.2f" % (np.mean(telaviv['content_len']))))
print('tallinn tweet length mean', ("%.2f" % (np.mean(tallinn['content_len']))))
print('all_public tweet length mean', ("%.2f" % (np.mean(all_public['content_len']))))
print('all_corpo tweet length mean', ("%.2f" % (np.mean(all_corpo['content_len']))))
print('all_startup tweet length mean', ("%.2f" % (np.mean(all_startup['content_len']))))
print('all_academic tweet length mean', ("%.2f" % (np.mean(all_academic['content_len']))))
print('all_civil tweet length mean', ("%.2f" % (np.mean(all_civil['content_len']))))
print('all_media tweet length mean', ("%.2f" % (np.mean(all_media['content_len']))))
print('all_city tweet length mean', ("%.2f" % (np.mean(all_city['content_len']))))
print('global tweet length mean', ("%.2f" % (np.mean(global_['content_len']))))

print('tw_public tweet length std', ("%.2f" % (np.std(tw_public['content_len']))))
print('tw_corpo tweet length std', ("%.2f" % (np.std(tw_corpo['content_len']))))
print('tw_startup tweet length std', ("%.2f" % (np.std(tw_startup['content_len']))))
print('tw_academic tweet length std', ("%.2f" % (np.std(tw_academic['content_len']))))
print('tw_civil tweet length std', ("%.2f" % (np.std(tw_civil['content_len']))))
print('tw_media tweet length std', ("%.2f" % (np.std(tw_media['content_len']))))
print('il_public tweet length std', ("%.2f" % (np.std(il_public['content_len']))))
print('il_corpo tweet length std', ("%.2f" % (np.std(il_corpo['content_len']))))
print('il_startup tweet length std', ("%.2f" % (np.std(il_startup['content_len']))))
print('il_academic tweet length std', ("%.2f" % (np.std(il_academic['content_len']))))
print('il_civil tweet length std', ("%.2f" % (np.std(il_civil['content_len']))))
print('il_media tweet length std', ("%.2f" % (np.std(il_media['content_len']))))
print('ee_public tweet length std', ("%.2f" % (np.std(ee_public['content_len']))))
print('ee_corpo tweet length std', ("%.2f" % (np.std(ee_corpo['content_len']))))
print('ee_startup tweet length std', ("%.2f" % (np.std(ee_startup['content_len']))))
print('ee_academic tweet length std', ("%.2f" % (np.std(ee_academic['content_len']))))
print('ee_civil tweet length std', ("%.2f" % (np.std(ee_civil['content_len']))))
print('ee_media tweet length std', ("%.2f" % (np.std(ee_media['content_len']))))
print('taipei tweet length std', ("%.2f" % (np.std(taipei['content_len']))))
print('telaviv tweet length std', ("%.2f" % (np.std(telaviv['content_len']))))
print('tallinn tweet length std', ("%.2f" % (np.std(tallinn['content_len']))))
print('all_public tweet length std', ("%.2f" % (np.std(all_public['content_len']))))
print('all_corpo tweet length std', ("%.2f" % (np.std(all_corpo['content_len']))))
print('all_startup tweet length std', ("%.2f" % (np.std(all_startup['content_len']))))
print('all_academic tweet length std', ("%.2f" % (np.std(all_academic['content_len']))))
print('all_civil tweet length std', ("%.2f" % (np.std(all_civil['content_len']))))
print('all_media tweet length std', ("%.2f" % (np.std(all_media['content_len']))))
print('all_city tweet length std', ("%.2f" % (np.std(all_city['content_len']))))
print('global tweet length std', ("%.2f" % (np.std(global_['content_len']))))

tw_public tweet length mean 159.26
tw_corpo tweet length mean 137.47
tw_startup tweet length mean 122.51
tw_academic tweet length mean 157.50
tw_civil tweet length mean 156.06
tw_media tweet length mean 120.49
il_public tweet length mean 116.61
il_corpo tweet length mean 209.62
il_startup tweet length mean 128.68
il_academic tweet length mean 147.13
il_civil tweet length mean 106.91
il_media tweet length mean 143.70
ee_public tweet length mean 134.45
ee_corpo tweet length mean 143.12
ee_startup tweet length mean 184.24
ee_academic tweet length mean 136.34
ee_civil tweet length mean 181.92
ee_media tweet length mean 82.50
taipei tweet length mean 144.49
telaviv tweet length mean 140.12
tallinn tweet length mean 147.07
all_public tweet length mean 137.98
all_corpo tweet length mean 166.34
all_startup tweet length mean 136.13
all_academic tweet length mean 146.44
all_civil tweet length mean 122.23
all_media tweet length mean 114.50
all_city tweet length mean 143.02
global tweet length mea

In [18]:
#add a column with number of words for each tweet
tw_public['num_word'] = tw_public['content'].apply(lambda x: len(x.split()))
tw_corpo['num_word'] = tw_corpo['content'].apply(lambda x: len(x.split()))
tw_startup['num_word'] = tw_startup['content'].apply(lambda x: len(x.split()))
tw_academic['num_word'] = tw_academic['content'].apply(lambda x: len(x.split()))
tw_civil['num_word'] = tw_civil['content'].apply(lambda x: len(x.split()))
tw_media['num_word'] = tw_media['content'].apply(lambda x: len(x.split()))
il_public['num_word'] = il_public['content'].apply(lambda x: len(x.split()))
il_corpo['num_word'] = il_corpo['content'].apply(lambda x: len(x.split()))
il_startup['num_word'] = il_startup['content'].apply(lambda x: len(x.split()))
il_academic['num_word'] = il_academic['content'].apply(lambda x: len(x.split()))
il_civil['num_word'] = il_civil['content'].apply(lambda x: len(x.split()))
il_media['num_word'] = il_media['content'].apply(lambda x: len(x.split()))
ee_public['num_word'] = ee_public['content'].apply(lambda x: len(x.split()))
ee_corpo['num_word'] = ee_corpo['content'].apply(lambda x: len(x.split()))
ee_startup['num_word'] = ee_startup['content'].apply(lambda x: len(x.split()))
ee_academic['num_word'] = ee_academic['content'].apply(lambda x: len(x.split()))
ee_civil['num_word'] = ee_civil['content'].apply(lambda x: len(x.split()))
ee_media['num_word'] = ee_media['content'].apply(lambda x: len(x.split()))
taipei['num_word'] = taipei['content'].apply(lambda x: len(x.split()))
telaviv['num_word'] = telaviv['content'].apply(lambda x: len(x.split()))
tallinn['num_word'] = tallinn['content'].apply(lambda x: len(x.split()))
all_public['num_word'] = all_public['content'].apply(lambda x: len(x.split()))
all_corpo['num_word'] = all_corpo['content'].apply(lambda x: len(x.split()))
all_startup['num_word'] = all_startup['content'].apply(lambda x: len(x.split()))
all_academic['num_word'] = all_academic['content'].apply(lambda x: len(x.split()))
all_civil['num_word'] = all_civil['content'].apply(lambda x: len(x.split()))
all_media['num_word'] = all_media['content'].apply(lambda x: len(x.split()))
all_city['num_word'] = all_city['content'].apply(lambda x: len(x.split()))
global_['num_word'] = global_['content'].apply(lambda x: len(x.split()))

In [19]:
#add a column with number of sentences for each tweet
tw_public['num_sentence'] = tw_public['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
tw_corpo['num_sentence'] = tw_corpo['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
tw_startup['num_sentence'] = tw_startup['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
tw_academic['num_sentence'] = tw_academic['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
tw_civil['num_sentence'] = tw_civil['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
tw_media['num_sentence'] = tw_media['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
il_public['num_sentence'] = il_public['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
il_corpo['num_sentence'] = il_corpo['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
il_startup['num_sentence'] = il_startup['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
il_academic['num_sentence'] = il_academic['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
il_civil['num_sentence'] = il_civil['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
il_media['num_sentence'] = il_media['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
ee_public['num_sentence'] = ee_public['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
ee_corpo['num_sentence'] = ee_corpo['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
ee_startup['num_sentence'] = ee_startup['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
ee_academic['num_sentence'] = ee_academic['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
ee_civil['num_sentence'] = ee_civil['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
ee_media['num_sentence'] = ee_media['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
taipei['num_sentence'] = taipei['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
telaviv['num_sentence'] = telaviv['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
tallinn['num_sentence'] = tallinn['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
all_public['num_sentence'] = all_public['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
all_corpo['num_sentence'] = all_corpo['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
all_startup['num_sentence'] = all_startup['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
all_academic['num_sentence'] = all_academic['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
all_civil['num_sentence'] = all_civil['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
all_media['num_sentence'] = all_media['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
all_city['num_sentence'] = all_city['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))
global_['num_sentence'] = global_['content'].apply(lambda x: len(re.split( '~ ...' ,'~'.join(x.split('.')))))

In [20]:
#calculare means and standard devs
print('tw_public num_words_mean', ("%.2f" % (np.mean(tw_public['num_word']))))
print('tw_public num_words_std', ("%.2f" % (np.std(tw_public['num_word']))))
print('tw_public num_sentences_mean', ("%.2f" % (np.mean(tw_public['num_sentence']))))
print('tw_public num_sentences_std', ("%.2f" % (np.std(tw_public['num_sentence']))))
print('tw_corpo num_words_mean', ("%.2f" % (np.mean(tw_corpo['num_word']))))
print('tw_corpo num_words_std', ("%.2f" % (np.std(tw_corpo['num_word']))))
print('tw_corpo num_sentences_mean', ("%.2f" % (np.mean(tw_corpo['num_sentence']))))
print('tw_corpo num_sentences_std', ("%.2f" % (np.std(tw_corpo['num_sentence']))))
print('tw_startup num_words_mean', ("%.2f" % (np.mean(tw_startup['num_word']))))
print('tw_startup num_words_std', ("%.2f" % (np.std(tw_startup['num_word']))))
print('tw_startup num_sentences_mean', ("%.2f" % (np.mean(tw_startup['num_sentence']))))
print('tw_startup num_sentences_std', ("%.2f" % (np.std(tw_startup['num_sentence']))))
print('tw_academic num_words_mean', ("%.2f" % (np.mean(tw_academic['num_word']))))
print('tw_academic num_words_std', ("%.2f" % (np.std(tw_academic['num_word']))))
print('tw_academic num_sentences_mean', ("%.2f" % (np.mean(tw_academic['num_sentence']))))
print('tw_academic num_sentences_std', ("%.2f" % (np.std(tw_academic['num_sentence']))))
print('tw_civil num_words_mean', ("%.2f" % (np.mean(tw_civil['num_word']))))
print('tw_civil num_words_std', ("%.2f" % (np.std(tw_civil['num_word']))))
print('tw_civil num_sentences_mean', ("%.2f" % (np.mean(tw_civil['num_sentence']))))
print('tw_civil num_sentences_std', ("%.2f" % (np.std(tw_civil['num_sentence']))))
print('tw_media num_words_mean', ("%.2f" % (np.mean(tw_media['num_word']))))
print('tw_media num_words_std', ("%.2f" % (np.std(tw_media['num_word']))))
print('tw_media num_sentences_mean', ("%.2f" % (np.mean(tw_media['num_sentence']))))
print('tw_media num_sentences_std', ("%.2f" % (np.std(tw_media['num_sentence']))))
print('il_public num_words_mean', ("%.2f" % (np.mean(il_public['num_word']))))
print('il_public num_words_std', ("%.2f" % (np.std(il_public['num_word']))))
print('il_public num_sentences_mean', ("%.2f" % (np.mean(il_public['num_sentence']))))
print('il_public num_sentences_std', ("%.2f" % (np.std(il_public['num_sentence']))))
print('il_corpo num_words_mean', ("%.2f" % (np.mean(il_corpo['num_word']))))
print('il_corpo num_words_std', ("%.2f" % (np.std(il_corpo['num_word']))))
print('il_corpo num_sentences_mean', ("%.2f" % (np.mean(il_corpo['num_sentence']))))
print('il_corpo num_sentences_std', ("%.2f" % (np.std(il_corpo['num_sentence']))))
print('il_startup num_words_mean', ("%.2f" % (np.mean(il_startup['num_word']))))
print('il_startup num_words_std', ("%.2f" % (np.std(il_startup['num_word']))))
print('il_startup num_sentences_mean', ("%.2f" % (np.mean(il_startup['num_sentence']))))
print('il_startup num_sentences_std', ("%.2f" % (np.std(il_startup['num_sentence']))))
print('il_academic num_words_mean', ("%.2f" % (np.mean(il_academic['num_word']))))
print('il_academic num_words_std', ("%.2f" % (np.std(il_academic['num_word']))))
print('il_academic num_sentences_mean', ("%.2f" % (np.mean(il_academic['num_sentence']))))
print('il_academic num_sentences_std', ("%.2f" % (np.std(il_academic['num_sentence']))))
print('il_civil num_words_mean', ("%.2f" % (np.mean(il_civil['num_word']))))
print('il_civil num_words_std', ("%.2f" % (np.std(il_civil['num_word']))))
print('il_civil num_sentences_mean', ("%.2f" % (np.mean(il_civil['num_sentence']))))
print('il_civil num_sentences_std', ("%.2f" % (np.std(il_civil['num_sentence']))))
print('il_media num_words_mean', ("%.2f" % (np.mean(il_media['num_word']))))
print('il_media num_words_std', ("%.2f" % (np.std(il_media['num_word']))))
print('il_media num_sentences_mean', ("%.2f" % (np.mean(il_media['num_sentence']))))
print('il_media num_sentences_std', ("%.2f" % (np.std(il_media['num_sentence']))))
print('ee_public num_words_mean', ("%.2f" % (np.mean(ee_public['num_word']))))
print('ee_public num_words_std', ("%.2f" % (np.std(ee_public['num_word']))))
print('ee_public num_sentences_mean', ("%.2f" % (np.mean(ee_public['num_sentence']))))
print('ee_public num_sentences_std', ("%.2f" % (np.std(ee_public['num_sentence']))))
print('ee_corpo num_words_mean', ("%.2f" % (np.mean(ee_corpo['num_word']))))
print('ee_corpo num_words_std', ("%.2f" % (np.std(ee_corpo['num_word']))))
print('ee_corpo num_sentences_mean', ("%.2f" % (np.mean(ee_corpo['num_sentence']))))
print('ee_corpo num_sentences_std', ("%.2f" % (np.std(ee_corpo['num_sentence']))))
print('ee_startup num_words_mean', ("%.2f" % (np.mean(ee_startup['num_word']))))
print('ee_startup num_words_std', ("%.2f" % (np.std(ee_startup['num_word']))))
print('ee_startup num_sentences_mean', ("%.2f" % (np.mean(ee_startup['num_sentence']))))
print('ee_startup num_sentences_std', ("%.2f" % (np.std(ee_startup['num_sentence']))))
print('ee_academic num_words_mean', ("%.2f" % (np.mean(ee_academic['num_word']))))
print('ee_academic num_words_std', ("%.2f" % (np.std(ee_academic['num_word']))))
print('ee_academic num_sentences_mean', ("%.2f" % (np.mean(ee_academic['num_sentence']))))
print('ee_academic num_sentences_std', ("%.2f" % (np.std(ee_academic['num_sentence']))))
print('ee_civil num_words_mean', ("%.2f" % (np.mean(ee_civil['num_word']))))
print('ee_civil num_words_std', ("%.2f" % (np.std(ee_civil['num_word']))))
print('ee_civil num_sentences_mean', ("%.2f" % (np.mean(ee_civil['num_sentence']))))
print('ee_civil num_sentences_std', ("%.2f" % (np.std(ee_civil['num_sentence']))))
print('ee_media num_words_mean', ("%.2f" % (np.mean(ee_media['num_word']))))
print('ee_media num_words_std', ("%.2f" % (np.std(ee_media['num_word']))))
print('ee_media num_sentences_mean', ("%.2f" % (np.mean(ee_media['num_sentence']))))
print('ee_media num_sentences_std', ("%.2f" % (np.std(ee_media['num_sentence']))))
print('taipei num_words_mean', ("%.2f" % (np.mean(taipei['num_word']))))
print('taipei num_words_std', ("%.2f" % (np.std(taipei['num_word']))))
print('taipei num_sentences_mean', ("%.2f" % (np.mean(taipei['num_sentence']))))
print('taipei num_sentences_std', ("%.2f" % (np.std(taipei['num_sentence']))))
print('telaviv num_words_mean', ("%.2f" % (np.mean(telaviv['num_word']))))
print('telaviv num_words_std', ("%.2f" % (np.std(telaviv['num_word']))))
print('telaviv num_sentences_mean', ("%.2f" % (np.mean(telaviv['num_sentence']))))
print('tallinn num_words_mean', ("%.2f" % (np.mean(tallinn['num_word']))))
print('tallinn num_words_std', ("%.2f" % (np.std(tallinn['num_word']))))
print('tallinn num_sentences_mean', ("%.2f" % (np.mean(tallinn['num_sentence']))))
print('tallinn num_sentences_std', ("%.2f" % (np.std(tallinn['num_sentence']))))
print('all_public num_words_mean', ("%.2f" % (np.mean(all_public['num_word']))))
print('all_public num_words_std', ("%.2f" % (np.std(all_public['num_word']))))
print('all_public num_sentences_mean', ("%.2f" % (np.mean(all_public['num_sentence']))))
print('all_public num_sentences_std', ("%.2f" % (np.std(all_public['num_sentence']))))
print('all_corpo num_words_mean', ("%.2f" % (np.mean(all_corpo['num_word']))))
print('all_corpo num_words_std', ("%.2f" % (np.std(all_corpo['num_word']))))
print('all_corpo num_sentences_mean', ("%.2f" % (np.mean(all_corpo['num_sentence']))))
print('all_corpo num_sentences_std', ("%.2f" % (np.std(all_corpo['num_sentence']))))
print('all_startup num_words_mean', ("%.2f" % (np.mean(all_startup['num_word']))))
print('all_startup num_words_std', ("%.2f" % (np.std(all_startup['num_word']))))
print('all_startup num_sentences_mean', ("%.2f" % (np.mean(all_startup['num_sentence']))))
print('all_startup num_sentences_std', ("%.2f" % (np.std(all_startup['num_sentence']))))
print('all_academic num_words_mean', ("%.2f" % (np.mean(all_academic['num_word']))))
print('all_academic num_words_std', ("%.2f" % (np.std(all_academic['num_word']))))
print('all_academic num_sentences_mean', ("%.2f" % (np.mean(all_academic['num_sentence']))))
print('all_academic num_sentences_std', ("%.2f" % (np.std(all_academic['num_sentence']))))
print('all_civil num_words_mean', ("%.2f" % (np.mean(all_civil['num_word']))))
print('all_civil num_words_std', ("%.2f" % (np.std(all_civil['num_word']))))
print('all_civil num_sentences_mean', ("%.2f" % (np.mean(all_civil['num_sentence']))))
print('all_civil num_sentences_std', ("%.2f" % (np.std(all_civil['num_sentence']))))
print('all_media num_words_mean', ("%.2f" % (np.mean(all_media['num_word']))))
print('all_media num_words_std', ("%.2f" % (np.std(all_media['num_word']))))
print('all_media num_sentences_mean', ("%.2f" % (np.mean(all_media['num_sentence']))))
print('all_media num_sentences_std', ("%.2f" % (np.std(all_media['num_sentence']))))
print('all_city num_words_mean', ("%.2f" % (np.mean(all_city['num_word']))))
print('all_city num_words_std', ("%.2f" % (np.std(all_city['num_word']))))
print('all_city num_sentences_mean', ("%.2f" % (np.mean(all_city['num_sentence']))))
print('all_city num_sentences_std', ("%.2f" % (np.std(all_city['num_sentence']))))
print('global_ num_words_mean', ("%.2f" % (np.mean(global_['num_word']))))
print('global_ num_words_std', ("%.2f" % (np.std(global_['num_word']))))
print('global_ num_sentences_mean', ("%.2f" % (np.mean(global_['num_sentence']))))
print('global_ num_sentences_std', ("%.2f" % (np.std(global_['num_sentence']))))

tw_public num_words_mean 19.76
tw_public num_words_std 11.09
tw_public num_sentences_mean 1.77
tw_public num_sentences_std 1.01
tw_corpo num_words_mean 19.61
tw_corpo num_words_std 9.78
tw_corpo num_sentences_mean 1.61
tw_corpo num_sentences_std 0.73
tw_startup num_words_mean 15.59
tw_startup num_words_std 5.90
tw_startup num_sentences_mean 1.37
tw_startup num_sentences_std 0.64
tw_academic num_words_mean 21.41
tw_academic num_words_std 11.23
tw_academic num_sentences_mean 1.57
tw_academic num_sentences_std 0.86
tw_civil num_words_mean 20.84
tw_civil num_words_std 9.58
tw_civil num_sentences_mean 1.47
tw_civil num_sentences_std 0.71
tw_media num_words_mean 12.90
tw_media num_words_std 3.81
tw_media num_sentences_mean 1.20
tw_media num_sentences_std 0.43
il_public num_words_mean 18.41
il_public num_words_std 10.55
il_public num_sentences_mean 1.81
il_public num_sentences_std 0.92
il_corpo num_words_mean 26.86
il_corpo num_words_std 9.13
il_corpo num_sentences_mean 2.16
il_corpo num_sent

In [21]:
## create function for finding average length of words per tweet

def get_avg_word_len(x):
    words = x.split()
    word_len = 0
    for word in words:
        word_len = word_len + len(word)
        
    return word_len / len(words)

In [22]:
#add a column with average word length for each tweet
tw_public['avg_word_len'] = tw_public['content'].apply(lambda x: get_avg_word_len(x))
tw_corpo['avg_word_len'] = tw_corpo['content'].apply(lambda x: get_avg_word_len(x))
tw_startup['avg_word_len'] = tw_startup['content'].apply(lambda x: get_avg_word_len(x))
tw_academic['avg_word_len'] = tw_academic['content'].apply(lambda x: get_avg_word_len(x))
tw_civil['avg_word_len'] = tw_civil['content'].apply(lambda x: get_avg_word_len(x))
tw_media['avg_word_len'] = tw_media['content'].apply(lambda x: get_avg_word_len(x))
il_public['avg_word_len'] = il_public['content'].apply(lambda x: get_avg_word_len(x))
il_corpo['avg_word_len'] = il_corpo['content'].apply(lambda x: get_avg_word_len(x))
il_startup['avg_word_len'] = il_startup['content'].apply(lambda x: get_avg_word_len(x))
il_academic['avg_word_len'] = il_academic['content'].apply(lambda x: get_avg_word_len(x))
il_civil['avg_word_len'] = il_civil['content'].apply(lambda x: get_avg_word_len(x))
il_media['avg_word_len'] = il_media['content'].apply(lambda x: get_avg_word_len(x))
ee_public['avg_word_len'] = ee_public['content'].apply(lambda x: get_avg_word_len(x))
ee_corpo['avg_word_len'] = ee_corpo['content'].apply(lambda x: get_avg_word_len(x))
ee_startup['avg_word_len'] = ee_startup['content'].apply(lambda x: get_avg_word_len(x))
ee_academic['avg_word_len'] = ee_academic['content'].apply(lambda x: get_avg_word_len(x))
ee_civil['avg_word_len'] = ee_civil['content'].apply(lambda x: get_avg_word_len(x))
ee_media['avg_word_len'] = ee_media['content'].apply(lambda x: get_avg_word_len(x))
taipei['avg_word_len'] = taipei['content'].apply(lambda x: get_avg_word_len(x))
telaviv['avg_word_len'] = telaviv['content'].apply(lambda x: get_avg_word_len(x))
tallinn['avg_word_len'] = tallinn['content'].apply(lambda x: get_avg_word_len(x))
all_public['avg_word_len'] = all_public['content'].apply(lambda x: get_avg_word_len(x))
all_corpo['avg_word_len'] = all_corpo['content'].apply(lambda x: get_avg_word_len(x))
all_startup['avg_word_len'] = all_startup['content'].apply(lambda x: get_avg_word_len(x))
all_academic['avg_word_len'] = all_academic['content'].apply(lambda x: get_avg_word_len(x))
all_civil['avg_word_len'] = all_civil['content'].apply(lambda x: get_avg_word_len(x))
all_media['avg_word_len'] = all_media['content'].apply(lambda x: get_avg_word_len(x))
all_city['avg_word_len'] = all_city['content'].apply(lambda x: get_avg_word_len(x))
global_['avg_word_len'] = global_['content'].apply(lambda x: get_avg_word_len(x))

In [23]:
#calculare means and standard devs for each new columns
print('tw_public average word length mean', ("%.2f" % (np.mean(tw_public['avg_word_len']))))
print('tw_corpo average word length mean', ("%.2f" % (np.mean(tw_corpo['avg_word_len']))))
print('tw_startup average word length mean', ("%.2f" % (np.mean(tw_startup['avg_word_len']))))
print('tw_academic average word length mean', ("%.2f" % (np.mean(tw_academic['avg_word_len']))))
print('tw_civil average word length mean', ("%.2f" % (np.mean(tw_civil['avg_word_len']))))
print('tw_media average word length mean', ("%.2f" % (np.mean(tw_media['avg_word_len']))))
print('il_public average word length mean', ("%.2f" % (np.mean(il_public['avg_word_len']))))
print('il_corpo average word length mean', ("%.2f" % (np.mean(il_corpo['avg_word_len']))))
print('il_startup average word length mean', ("%.2f" % (np.mean(il_startup['avg_word_len']))))
print('il_academic average word length mean', ("%.2f" % (np.mean(il_academic['avg_word_len']))))
print('il_civil average word length mean', ("%.2f" % (np.mean(il_civil['avg_word_len']))))
print('il_media average word length mean', ("%.2f" % (np.mean(il_media['avg_word_len']))))
print('ee_public average word length mean', ("%.2f" % (np.mean(ee_public['avg_word_len']))))
print('ee_corpo average word length mean', ("%.2f" % (np.mean(ee_corpo['avg_word_len']))))
print('ee_startup average word length mean', ("%.2f" % (np.mean(ee_startup['avg_word_len']))))
print('ee_academic average word length mean', ("%.2f" % (np.mean(ee_academic['avg_word_len']))))
print('ee_civil average word length mean', ("%.2f" % (np.mean(ee_civil['avg_word_len']))))
print('ee_media average word length mean', ("%.2f" % (np.mean(ee_media['avg_word_len']))))
print('taipei average word length mean', ("%.2f" % (np.mean(taipei['avg_word_len']))))
print('telaviv average word length mean', ("%.2f" % (np.mean(telaviv['avg_word_len']))))
print('tallinn average word length mean', ("%.2f" % (np.mean(tallinn['avg_word_len']))))
print('all_public average word length mean', ("%.2f" % (np.mean(all_public['avg_word_len']))))
print('all_corpo average word length mean', ("%.2f" % (np.mean(all_corpo['avg_word_len']))))
print('all_startup average word length mean', ("%.2f" % (np.mean(all_startup['avg_word_len']))))
print('all_academic average word length mean', ("%.2f" % (np.mean(all_academic['avg_word_len']))))
print('all_civil average word length mean', ("%.2f" % (np.mean(all_civil['avg_word_len']))))
print('all_media average word length mean', ("%.2f" % (np.mean(all_media['avg_word_len']))))
print('all_city average word length mean', ("%.2f" % (np.mean(all_city['avg_word_len']))))
print('global average word length mean', ("%.2f" % (np.mean(global_['avg_word_len']))))

print('tw_public average word length std', ("%.2f" % (np.std(tw_public['avg_word_len']))))
print('tw_corpo average word length std', ("%.2f" % (np.std(tw_corpo['avg_word_len']))))
print('tw_startup average word length std', ("%.2f" % (np.std(tw_startup['avg_word_len']))))
print('tw_academic average word length std', ("%.2f" % (np.std(tw_academic['avg_word_len']))))
print('tw_civil average word length std', ("%.2f" % (np.std(tw_civil['avg_word_len']))))
print('tw_media average word length std', ("%.2f" % (np.std(tw_media['avg_word_len']))))
print('il_public average word length std', ("%.2f" % (np.std(il_public['avg_word_len']))))
print('il_corpo average word length std', ("%.2f" % (np.std(il_corpo['avg_word_len']))))
print('il_startup average word length std', ("%.2f" % (np.std(il_startup['avg_word_len']))))
print('il_academic average word length std', ("%.2f" % (np.std(il_academic['avg_word_len']))))
print('il_civil average word length std', ("%.2f" % (np.std(il_civil['avg_word_len']))))
print('il_media average word length std', ("%.2f" % (np.std(il_media['avg_word_len']))))
print('ee_public average word length std', ("%.2f" % (np.std(ee_public['avg_word_len']))))
print('ee_corpo average word length std', ("%.2f" % (np.std(ee_corpo['avg_word_len']))))
print('ee_startup average word length std', ("%.2f" % (np.std(ee_startup['avg_word_len']))))
print('ee_academic average word length std', ("%.2f" % (np.std(ee_academic['avg_word_len']))))
print('ee_civil average word length std', ("%.2f" % (np.std(ee_civil['avg_word_len']))))
print('ee_media average word length std', ("%.2f" % (np.std(ee_media['avg_word_len']))))
print('taipei average word length std', ("%.2f" % (np.std(taipei['avg_word_len']))))
print('telaviv average word length std', ("%.2f" % (np.std(telaviv['avg_word_len']))))
print('tallinn average word length std', ("%.2f" % (np.std(tallinn['avg_word_len']))))
print('all_public average word length std', ("%.2f" % (np.std(all_public['avg_word_len']))))
print('all_corpo average word length std', ("%.2f" % (np.std(all_corpo['avg_word_len']))))
print('all_startup average word length std', ("%.2f" % (np.std(all_startup['avg_word_len']))))
print('all_academic average word length std', ("%.2f" % (np.std(all_academic['avg_word_len']))))
print('all_civil average word length std', ("%.2f" % (np.std(all_civil['avg_word_len']))))
print('all_media average word length std', ("%.2f" % (np.std(all_media['avg_word_len']))))
print('all_city average word length std', ("%.2f" % (np.std(all_city['avg_word_len']))))
print('global average word length std', ("%.2f" % (np.std(global_['avg_word_len']))))

tw_public average word length mean 9.10
tw_corpo average word length mean 6.33
tw_startup average word length mean 7.24
tw_academic average word length mean 7.30
tw_civil average word length mean 7.77
tw_media average word length mean 8.62
il_public average word length mean 5.89
il_corpo average word length mean 7.04
il_startup average word length mean 6.18
il_academic average word length mean 7.39
il_civil average word length mean 6.58
il_media average word length mean 7.75
ee_public average word length mean 7.32
ee_corpo average word length mean 5.37
ee_startup average word length mean 6.48
ee_academic average word length mean 7.35
ee_civil average word length mean 7.20
ee_media average word length mean 9.54
taipei average word length mean 7.22
telaviv average word length mean 6.97
tallinn average word length mean 7.13
all_public average word length mean 7.55
all_corpo average word length mean 6.36
all_startup average word length mean 6.42
all_academic average word length mean 7.37
a

In [24]:
#check the columns of my datasets
tw_public.head()

tweet_id city_id            agent_id                twitter_profile  \
0     49185  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
1     49186  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
2     49187  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
3     49188  Taipei  706869314746327040  https://twitter.com/KP_Taipei   
4     49189  Taipei  706869314746327040  https://twitter.com/KP_Taipei   

                                           tweet_url  \
0  https://twitter.com/KP_Taipei/status/120929730...   
1  https://twitter.com/KP_Taipei/status/120894267...   
2  https://twitter.com/KP_Taipei/status/120892310...   
3  https://twitter.com/KP_Taipei/status/120793406...   
4  https://twitter.com/KP_Taipei/status/120757728...   

                                             content total_likes  \
0  On-behalf of the entire City Hall, I wish all ...         141   
1  Very exciting to watch Taipei’s development of...         197   
2  Recently I attended the #AsiaPacificMedicalAca...         134   
3  阿北提醒大家，避免傳染禽流感，早點施打流感疫苗。\n#阿北關心您\n#對抗流感大家一起來 h...         250   
4  It was a great honor to meet with the delegati...         151   

   total_retweet  identified_liker is_reply  ...  polarity subjectivity  \
0            NaN               NaN      NaN  ...  0.268466      0.63125   
1            NaN               NaN      NaN  ...  0.196667      0.50000   
2            NaN               NaN      NaN  ...  0.000000      0.32500   
3            NaN               NaN      NaN  ...  0.000000      0.00000   
4            NaN               NaN      NaN  ...  0.460000      0.61000   

  compound  neg    neu    pos  content_len  num_word  num_sentence  \
0   0.9168  0.0  0.685  0.315          215        30             2   
1   0.9348  0.0  0.561  0.439          213        29             3   
2   0.0000  0.0  1.000  0.000          293        39             3   
3   0.0000  0.0  1.000  0.000           66         4             1   
4   0.9100  0.0  0.758  0.242          279        39             3   

   avg_word_len  
0      6.166667  
1      6.379310  
2      6.487179  
3     15.750000  
4      6.153846  

[5 rows x 23 columns]

### use regex to clean the text - strings

In [25]:
# copy the original tweet in a new column where to process text cleaning
tw_public['text'] = tw_public['content']
tw_corpo['text'] = tw_corpo['content']
tw_startup['text'] = tw_startup['content']
tw_academic['text'] = tw_academic['content']
tw_civil['text'] = tw_civil['content']
tw_media['text'] = tw_media['content']
il_public['text'] = il_public['content']
il_corpo['text'] = il_corpo['content']
il_startup['text'] = il_startup['content']
il_academic['text'] = il_academic['content']
il_civil['text'] = il_civil['content']
il_media['text'] = il_media['content']
ee_public['text'] = ee_public['content']
ee_corpo['text'] = ee_corpo['content']
ee_startup['text'] = ee_startup['content']
ee_academic['text'] = ee_academic['content']
ee_civil['text'] = ee_civil['content']
ee_media['text'] = ee_media['content']
taipei['text'] = taipei['content']
telaviv['text'] = telaviv['content']
tallinn['text'] = tallinn['content']
all_public['text'] = all_public['content']
all_corpo['text'] = all_corpo['content']
all_startup['text'] = all_startup['content']
all_academic['text'] = all_academic['content']
all_civil['text'] = all_civil['content']
all_media['text'] = all_media['content']
all_city['text'] = all_city['content']
global_['text'] = global_['content']

In [26]:
# expanding contractions
contractions = contractions = { 
"ain't": "am not",
"aren't": "are not",
"can't": "cannot",
"can't've": "cannot have",
"'cause": "because",
"could've": "could have",
"couldn't": "could not",
"couldn't've": "could not have",
"didn't": "did not",
"doesn't": "does not",
"don't": "do not",
"hadn't": "had not",
"hadn't've": "had not have",
"hasn't": "has not",
"haven't": "have not",
"he'd": "he would",
"he'd've": "he would have",
"he'll": "he will",
"he'll've": "he will have",
"he's": "he is",
"how'd": "how did",
"how'd'y": "how do you",
"how'll": "how will",
"how's": "how is",
"I'd": "I would",
"I'd've": "I would have",
"I'll": "I will",
"I'll've": "I will have",
"I'm": "I am",
"I've": "I have",
"isn't": "is not",
"it'd": "it would",
"it'd've": "it would have",
"it'll": "it will",
"it'll've": "it will have",
"it's": "it is",
"let's": "let us",
"ma'am": "madam",
"mayn't": "may not",
"might've": "might have",
"mightn't": "might not",
"mightn't've": "might not have",
"must've": "must have",
"mustn't": "must not",
"mustn't've": "must not have",
"needn't": "need not",
"needn't've": "need not have",
"o'clock": "of the clock",
"oughtn't": "ought not",
"oughtn't've": "ought not have",
"shan't": "shall not",
"sha'n't": "shall not",
"shan't've": "shall not have",
"she'd": "she would",
"she'd've": "she would have",
"she'll": "she will",
"she'll've": "she will have",
"she's": "she is",
"should've": "should have",
"shouldn't": "should not",
"shouldn't've": "should not have",
"so've": "so have",
"so's": "so as / so is",
"that'd": "that would",
"that'd've": "that would have",
"that's": "that is",
"there'd": "there would",
"there'd've": "there would have",
"there's": "there is",
"they'd": "they would",
"they'd've": "they would have",
"they'll": "they will",
"they'll've": "they will have",
"they're": "they are",
"they've": "they have",
"to've": "to have",
"wasn't": "was not",
"we'd": "we would",
"we'd've": "we would have",
"we'll": "we will",
"we'll've": "we will have",
"we're": "we are",
"we've": "we have",
"weren't": "were not",
"what'll": "what will",
"what'll've": "what will have",
"what're": "what are",
"what's": "what is",
"what've": "what have",
"when's": "when is",
"when've": "when have",
"where'd": "where did",
"where's": "where is",
"where've": "where have",
"who'll": "who will",
"who'll've": "who will have",
"who's": "who is",
"who've": "who have",
"why's": "why is",
"why've": "why have",
"will've": "will have",
"won't": "will not",
"won't've": "will not have",
"would've": "would have",
"wouldn't": "would not",
"wouldn't've": "would not have",
"y'all": "you all",
"y'all'd": "you all would",
"y'all'd've": "you all would have",
"y'all're": "you all are",
"y'all've": "you all have",
"you'd": "you would",
"you'd've": "you would have",
"you'll": "you will",
"you'll've": "you will have",
"you're": "you are",
"you've": "you have"
}

In [27]:
def cont_to_exp(x):
    if type(x) is str:
        x = x.replace('\\','')
        for key in contractions:
            value = contractions[key]
            x = x.replace(key,value)
        return x
    else:
        return x

In [28]:
tw_public['text'] = tw_public['text'].apply(lambda x: cont_to_exp(x))
tw_corpo['text'] = tw_corpo['text'].apply(lambda x: cont_to_exp(x))
tw_startup['text'] = tw_startup['text'].apply(lambda x: cont_to_exp(x))
tw_academic['text'] = tw_academic['text'].apply(lambda x: cont_to_exp(x))
tw_civil['text'] = tw_civil['text'].apply(lambda x: cont_to_exp(x))
tw_media['text'] = tw_media['text'].apply(lambda x: cont_to_exp(x))
il_public['text'] = il_public['text'].apply(lambda x: cont_to_exp(x))
il_corpo['text'] = il_corpo['text'].apply(lambda x: cont_to_exp(x))
il_startup['text'] = il_startup['text'].apply(lambda x: cont_to_exp(x))
il_academic['text'] = il_academic['text'].apply(lambda x: cont_to_exp(x))
il_civil['text'] = il_civil['text'].apply(lambda x: cont_to_exp(x))
il_media['text'] = il_media['text'].apply(lambda x: cont_to_exp(x))
ee_public['text'] = ee_public['text'].apply(lambda x: cont_to_exp(x))
ee_corpo['text'] = ee_corpo['text'].apply(lambda x: cont_to_exp(x))
ee_startup['text'] = ee_startup['text'].apply(lambda x: cont_to_exp(x))
ee_academic['text'] = ee_academic['text'].apply(lambda x: cont_to_exp(x))
ee_civil['text'] = ee_civil['text'].apply(lambda x: cont_to_exp(x))
ee_media['text'] = ee_media['text'].apply(lambda x: cont_to_exp(x))
taipei['text'] = taipei['text'].apply(lambda x: cont_to_exp(x))
telaviv['text'] = telaviv['text'].apply(lambda x: cont_to_exp(x))
tallinn['text'] = tallinn['text'].apply(lambda x: cont_to_exp(x))
all_public['text'] = all_public['text'].apply(lambda x: cont_to_exp(x))
all_corpo['text'] = all_corpo['text'].apply(lambda x: cont_to_exp(x))
all_startup['text'] = all_startup['text'].apply(lambda x: cont_to_exp(x))
all_academic['text'] = all_academic['text'].apply(lambda x: cont_to_exp(x))
all_civil['text'] = all_civil['text'].apply(lambda x: cont_to_exp(x))
all_media['text'] = all_media['text'].apply(lambda x: cont_to_exp(x))
all_city['text'] = all_city['text'].apply(lambda x: cont_to_exp(x))
global_['text'] = global_['text'].apply(lambda x: cont_to_exp(x))

In [29]:
#lower characters
tw_public['text'] = tw_public['text'].str.lower()
tw_corpo['text'] = tw_corpo['text'].str.lower()
tw_startup['text'] = tw_startup['text'].str.lower()
tw_academic['text'] = tw_academic['text'].str.lower()
tw_civil['text'] = tw_civil['text'].str.lower()
tw_media['text'] = tw_media['text'].str.lower()
il_public['text'] = il_public['text'].str.lower()
il_corpo['text'] = il_corpo['text'].str.lower()
il_startup['text'] = il_startup['text'].str.lower()
il_academic['text'] = il_academic['text'].str.lower()
il_civil['text'] = il_civil['text'].str.lower()
il_media['text'] = il_media['text'].str.lower()
ee_public['text'] = ee_public['text'].str.lower()
ee_corpo['text'] = ee_corpo['text'].str.lower()
ee_startup['text'] = ee_startup['text'].str.lower()
ee_academic['text'] = ee_academic['text'].str.lower()
ee_civil['text'] = ee_civil['text'].str.lower()
ee_media['text'] = ee_media['text'].str.lower()
taipei['text'] = taipei['text'].str.lower()
telaviv['text'] = telaviv['text'].str.lower()
tallinn['text'] = tallinn['text'].str.lower()
all_public['text'] = all_public['text'].str.lower()
all_corpo['text'] = all_corpo['text'].str.lower()
all_startup['text'] = all_startup['text'].str.lower()
all_academic['text'] = all_academic['text'].str.lower()
all_civil['text'] = all_civil['text'].str.lower()
all_media['text'] = all_media['text'].str.lower()
all_city['text'] = all_city['text'].str.lower()
global_['text'] = global_['text'].str.lower()

In [30]:
# remove @mentions
tw_public['text'] = tw_public['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
tw_corpo['text'] = tw_corpo['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
tw_startup['text'] = tw_startup['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
tw_academic['text'] = tw_academic['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
tw_civil['text'] = tw_civil['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
tw_media['text'] = tw_media['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
il_public['text'] = il_public['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
il_corpo['text'] = il_corpo['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
il_startup['text'] = il_startup['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
il_academic['text'] = il_academic['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
il_civil['text'] = il_civil['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
il_media['text'] = il_media['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
ee_public['text'] = ee_public['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
ee_corpo['text'] = ee_corpo['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
ee_startup['text'] = ee_startup['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
ee_academic['text'] = ee_academic['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
ee_civil['text'] = ee_civil['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
ee_media['text'] = ee_media['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
taipei['text'] = taipei['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
telaviv['text'] = telaviv['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
tallinn['text'] = tallinn['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
all_public['text'] = all_public['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
all_corpo['text'] = all_corpo['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
all_startup['text'] = all_startup['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
all_academic['text'] = all_academic['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
all_civil['text'] = all_civil['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
all_media['text'] = all_media['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
all_city['text'] = all_city['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))
global_['text'] = global_['text'].apply(lambda x: re.sub(r'@[A-Za-z0-9]+','', str(x)))

In [31]:
# removing url links
tw_public['text'] = tw_public['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
tw_corpo['text'] = tw_corpo['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
tw_startup['text'] = tw_startup['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
tw_academic['text'] = tw_academic['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
tw_civil['text'] = tw_civil['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
tw_media['text'] = tw_media['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
il_public['text'] = il_public['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
il_corpo['text'] = il_corpo['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
il_startup['text'] = il_startup['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
il_academic['text'] = il_academic['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
il_civil['text'] = il_civil['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
il_media['text'] = il_media['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
ee_public['text'] = ee_public['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
ee_corpo['text'] = ee_corpo['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
ee_startup['text'] = ee_startup['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
ee_academic['text'] = ee_academic['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
ee_civil['text'] = ee_civil['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
ee_media['text'] = ee_media['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
taipei['text'] = taipei['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
telaviv['text'] = telaviv['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
tallinn['text'] = tallinn['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
all_public['text'] = all_public['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
all_corpo['text'] = all_corpo['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
all_startup['text'] = all_startup['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
all_academic['text'] = all_academic['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
all_civil['text'] = all_civil['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
all_media['text'] = all_media['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
all_city['text'] = all_city['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))
global_['text'] = global_['text'].apply(lambda x: re.sub(r'https?://[A-Za-z0-9./]+','', str(x)))

In [32]:
#remove digits
tw_public['text'] = tw_public['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
tw_corpo['text'] = tw_corpo['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
tw_startup['text'] = tw_startup['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
tw_academic['text'] = tw_academic['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
tw_civil['text'] = tw_civil['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
tw_media['text'] = tw_media['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
il_public['text'] = il_public['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
il_corpo['text'] = il_corpo['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
il_startup['text'] = il_startup['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
il_academic['text'] = il_academic['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
il_civil['text'] = il_civil['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
il_media['text'] = il_media['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
ee_public['text'] = ee_public['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
ee_corpo['text'] = ee_corpo['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
ee_startup['text'] = ee_startup['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
ee_academic['text'] = ee_academic['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
ee_civil['text'] = ee_civil['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
ee_media['text'] = ee_media['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
taipei['text'] = taipei['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
telaviv['text'] = telaviv['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
tallinn['text'] = tallinn['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
all_public['text'] = all_public['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
all_corpo['text'] = all_corpo['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
all_startup['text'] = all_startup['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
all_academic['text'] = all_academic['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
all_civil['text'] = all_civil['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
all_media['text'] = all_media['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
all_city['text'] = all_city['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))
global_['text'] = global_['text'].apply(lambda x: re.sub(r'[0-9]+','', str(x)))

In [33]:
#remove punctuation and symbols
tw_public['text'] = tw_public['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
tw_corpo['text'] = tw_corpo['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
tw_startup['text'] = tw_startup['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
tw_academic['text'] = tw_academic['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
tw_civil['text'] = tw_civil['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
tw_media['text'] = tw_media['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
il_public['text'] = il_public['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
il_corpo['text'] = il_corpo['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
il_startup['text'] = il_startup['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
il_academic['text'] = il_academic['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
il_civil['text'] = il_civil['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
il_media['text'] = il_media['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
ee_public['text'] = ee_public['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
ee_corpo['text'] = ee_corpo['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
ee_startup['text'] = ee_startup['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
ee_academic['text'] = ee_academic['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
ee_civil['text'] = ee_civil['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
ee_media['text'] = ee_media['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
taipei['text'] = taipei['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
telaviv['text'] = telaviv['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
tallinn['text'] = tallinn['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
all_public['text'] = all_public['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
all_corpo['text'] = all_corpo['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
all_startup['text'] = all_startup['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
all_academic['text'] = all_academic['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
all_civil['text'] = all_civil['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
all_media['text'] = all_media['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
all_city['text'] = all_city['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))
global_['text'] = global_['text'].apply(lambda x: re.sub(r'.,;?!/\@#&*$€£`§"+-%|:_’`()','', str(x)))

In [34]:
tw_public['text']

0       on-behalf of the entire city hall, i wish all ...
1       very exciting to watch taipei’s development of...
2       recently i attended the #asiapacificmedicalaca...
3           阿北提醒大家，避免傳染禽流感，早點施打流感疫苗。\n#阿北關心您\n#對抗流感大家一起來 
4       it was a great honor to meet with the delegati...
                              ...                        
1269    #柯p 宣布成立推特帳戶　_taipei\n\n#柯文哲 #taiwan #台湾 #poli...
1270    rt : mayor ko showing support of #taiwanese fo...
1271    mayor ko showing support of #taiwanese founder...
1272    thanks for joining us at taipei-silicon valley...
1273    earlier today i met with ko wen-je, the mayor ...
Name: text, Length: 1274, dtype: object

# token cleaning and operations

In [35]:
#Tokenize inside dataframes
tw_public['tokens'] = tw_public['text'].apply(lambda x: nltk.word_tokenize(x))
tw_corpo['tokens'] = tw_corpo['text'].apply(lambda x: nltk.word_tokenize(x))
tw_startup['tokens'] = tw_startup['text'].apply(lambda x: nltk.word_tokenize(x))
tw_academic['tokens'] = tw_academic['text'].apply(lambda x: nltk.word_tokenize(x))
tw_civil['tokens'] = tw_civil['text'].apply(lambda x: nltk.word_tokenize(x))
tw_media['tokens'] = tw_media['text'].apply(lambda x: nltk.word_tokenize(x))
il_public['tokens'] = il_public['text'].apply(lambda x: nltk.word_tokenize(x))
il_corpo['tokens'] = il_corpo['text'].apply(lambda x: nltk.word_tokenize(x))
il_startup['tokens'] = il_startup['text'].apply(lambda x: nltk.word_tokenize(x))
il_academic['tokens'] = il_academic['text'].apply(lambda x: nltk.word_tokenize(x))
il_civil['tokens'] = il_civil['text'].apply(lambda x: nltk.word_tokenize(x))
il_media['tokens'] = il_media['text'].apply(lambda x: nltk.word_tokenize(x))
ee_public['tokens'] = ee_public['text'].apply(lambda x: nltk.word_tokenize(x))
ee_corpo['tokens'] = ee_corpo['text'].apply(lambda x: nltk.word_tokenize(x))
ee_startup['tokens'] = ee_startup['text'].apply(lambda x: nltk.word_tokenize(x))
ee_academic['tokens'] = ee_academic['text'].apply(lambda x: nltk.word_tokenize(x))
ee_civil['tokens'] = ee_civil['text'].apply(lambda x: nltk.word_tokenize(x))
ee_media['tokens'] = ee_media['text'].apply(lambda x: nltk.word_tokenize(x))
taipei['tokens'] = taipei['text'].apply(lambda x: nltk.word_tokenize(x))
telaviv['tokens'] = telaviv['text'].apply(lambda x: nltk.word_tokenize(x))
tallinn['tokens'] = tallinn['text'].apply(lambda x: nltk.word_tokenize(x))
all_public['tokens'] = all_public['text'].apply(lambda x: nltk.word_tokenize(x))
all_corpo['tokens'] = all_corpo['text'].apply(lambda x: nltk.word_tokenize(x))
all_startup['tokens'] = all_startup['text'].apply(lambda x: nltk.word_tokenize(x))
all_academic['tokens'] = all_academic['text'].apply(lambda x: nltk.word_tokenize(x))
all_civil['tokens'] = all_civil['text'].apply(lambda x: nltk.word_tokenize(x))
all_media['tokens'] = all_media['text'].apply(lambda x: nltk.word_tokenize(x))
all_city['tokens'] = all_city['text'].apply(lambda x: nltk.word_tokenize(x))
global_['tokens'] = global_['text'].apply(lambda x: nltk.word_tokenize(x))

In [36]:
# remove stop words
a = stopwords.words('english')

tw_public['tokens'] = tw_public['tokens'].apply(lambda x: [item for item in x if item not in a])
tw_corpo['tokens'] = tw_corpo['tokens'].apply(lambda x: [item for item in x if item not in a])
tw_startup['tokens'] = tw_startup['tokens'].apply(lambda x: [item for item in x if item not in a])
tw_academic['tokens'] = tw_academic['tokens'].apply(lambda x: [item for item in x if item not in a])
tw_civil['tokens'] = tw_civil['tokens'].apply(lambda x: [item for item in x if item not in a])
tw_media['tokens'] = tw_media['tokens'].apply(lambda x: [item for item in x if item not in a])
il_public['tokens'] = il_public['tokens'].apply(lambda x: [item for item in x if item not in a])
il_corpo['tokens'] = il_corpo['tokens'].apply(lambda x: [item for item in x if item not in a])
il_startup['tokens'] = il_startup['tokens'].apply(lambda x: [item for item in x if item not in a])
il_academic['tokens'] = il_academic['tokens'].apply(lambda x: [item for item in x if item not in a])
il_civil['tokens'] = il_civil['tokens'].apply(lambda x: [item for item in x if item not in a])
il_media['tokens'] = il_media['tokens'].apply(lambda x: [item for item in x if item not in a])
ee_public['tokens'] = ee_public['tokens'].apply(lambda x: [item for item in x if item not in a])
ee_corpo['tokens'] = ee_corpo['tokens'].apply(lambda x: [item for item in x if item not in a])
ee_startup['tokens'] = ee_startup['tokens'].apply(lambda x: [item for item in x if item not in a])
ee_academic['tokens'] = ee_academic['tokens'].apply(lambda x: [item for item in x if item not in a])
ee_civil['tokens'] = ee_civil['tokens'].apply(lambda x: [item for item in x if item not in a])
ee_media['tokens'] = ee_media['tokens'].apply(lambda x: [item for item in x if item not in a])
taipei['tokens'] = taipei['tokens'].apply(lambda x: [item for item in x if item not in a])
telaviv['tokens'] = telaviv['tokens'].apply(lambda x: [item for item in x if item not in a])
tallinn['tokens'] = tallinn['tokens'].apply(lambda x: [item for item in x if item not in a])
all_public['tokens'] = all_public['tokens'].apply(lambda x: [item for item in x if item not in a])
all_corpo['tokens'] = all_corpo['tokens'].apply(lambda x: [item for item in x if item not in a])
all_startup['tokens'] = all_startup['tokens'].apply(lambda x: [item for item in x if item not in a])
all_academic['tokens'] = all_academic['tokens'].apply(lambda x: [item for item in x if item not in a])
all_civil['tokens'] = all_civil['tokens'].apply(lambda x: [item for item in x if item not in a])
all_media['tokens'] = all_media['tokens'].apply(lambda x: [item for item in x if item not in a])
all_city['tokens'] = all_city['tokens'].apply(lambda x: [item for item in x if item not in a])
global_['tokens'] = global_['tokens'].apply(lambda x: [item for item in x if item not in a])

In [37]:
#remove useless tokens
useless = ["com","#",'&','!',"gt","'re","\n","amp","als","'s","als", "etc",'\n', "\\n",'\\n\\n',']','[','.','...','“',',',"'","''",'th','…','“',':']

tw_public['tokens'] = tw_public['tokens'].apply(lambda x: [item for item in x if item not in useless])
tw_corpo['tokens'] = tw_corpo['tokens'].apply(lambda x: [item for item in x if item not in useless])
tw_startup['tokens'] = tw_startup['tokens'].apply(lambda x: [item for item in x if item not in useless])
tw_academic['tokens'] = tw_academic['tokens'].apply(lambda x: [item for item in x if item not in useless])
tw_civil['tokens'] = tw_civil['tokens'].apply(lambda x: [item for item in x if item not in useless])
tw_media['tokens'] = tw_media['tokens'].apply(lambda x: [item for item in x if item not in useless])
il_public['tokens'] = il_public['tokens'].apply(lambda x: [item for item in x if item not in useless])
il_corpo['tokens'] = il_corpo['tokens'].apply(lambda x: [item for item in x if item not in useless])
il_startup['tokens'] = il_startup['tokens'].apply(lambda x: [item for item in x if item not in useless])
il_academic['tokens'] = il_academic['tokens'].apply(lambda x: [item for item in x if item not in useless])
il_civil['tokens'] = il_civil['tokens'].apply(lambda x: [item for item in x if item not in useless])
il_media['tokens'] = il_media['tokens'].apply(lambda x: [item for item in x if item not in useless])
ee_public['tokens'] = ee_public['tokens'].apply(lambda x: [item for item in x if item not in useless])
ee_corpo['tokens'] = ee_corpo['tokens'].apply(lambda x: [item for item in x if item not in useless])
ee_startup['tokens'] = ee_startup['tokens'].apply(lambda x: [item for item in x if item not in useless])
ee_academic['tokens'] = ee_academic['tokens'].apply(lambda x: [item for item in x if item not in useless])
ee_civil['tokens'] = ee_civil['tokens'].apply(lambda x: [item for item in x if item not in useless])
ee_media['tokens'] = ee_media['tokens'].apply(lambda x: [item for item in x if item not in useless])
taipei['tokens'] = taipei['tokens'].apply(lambda x: [item for item in x if item not in useless])
telaviv['tokens'] = telaviv['tokens'].apply(lambda x: [item for item in x if item not in useless])
tallinn['tokens'] = tallinn['tokens'].apply(lambda x: [item for item in x if item not in useless])
all_public['tokens'] = all_public['tokens'].apply(lambda x: [item for item in x if item not in useless])
all_corpo['tokens'] = all_corpo['tokens'].apply(lambda x: [item for item in x if item not in useless])
all_startup['tokens'] = all_startup['tokens'].apply(lambda x: [item for item in x if item not in useless])
all_academic['tokens'] = all_academic['tokens'].apply(lambda x: [item for item in x if item not in useless])
all_civil['tokens'] = all_civil['tokens'].apply(lambda x: [item for item in x if item not in useless])
all_media['tokens'] = all_media['tokens'].apply(lambda x: [item for item in x if item not in useless])
all_city['tokens'] = all_city['tokens'].apply(lambda x: [item for item in x if item not in useless])
global_['tokens'] = global_['tokens'].apply(lambda x: [item for item in x if item not in useless])

In [38]:
#Lemmatization
lem = WordNetLemmatizer()

def lemma_wordnet(input):
    return [lem.lemmatize(w) for w in input]

tw_public['tokens'] = tw_public['tokens'].apply(lemma_wordnet)
tw_corpo['tokens'] = tw_corpo['tokens'].apply(lemma_wordnet)
tw_startup['tokens'] = tw_startup['tokens'].apply(lemma_wordnet)
tw_academic['tokens'] = tw_academic['tokens'].apply(lemma_wordnet)
tw_civil['tokens'] = tw_civil['tokens'].apply(lemma_wordnet)
tw_media['tokens'] = tw_media['tokens'].apply(lemma_wordnet)
il_public['tokens'] = il_public['tokens'].apply(lemma_wordnet)
il_corpo['tokens'] = il_corpo['tokens'].apply(lemma_wordnet)
il_startup['tokens'] = il_startup['tokens'].apply(lemma_wordnet)
il_academic['tokens'] = il_academic['tokens'].apply(lemma_wordnet)
il_civil['tokens'] = il_civil['tokens'].apply(lemma_wordnet)
il_media['tokens'] = il_media['tokens'].apply(lemma_wordnet)
ee_public['tokens'] = ee_public['tokens'].apply(lemma_wordnet)
ee_corpo['tokens'] = ee_corpo['tokens'].apply(lemma_wordnet)
ee_startup['tokens'] = ee_startup['tokens'].apply(lemma_wordnet)
ee_academic['tokens'] = ee_academic['tokens'].apply(lemma_wordnet)
ee_civil['tokens'] = ee_civil['tokens'].apply(lemma_wordnet)
ee_media['tokens'] = ee_media['tokens'].apply(lemma_wordnet)
taipei['tokens'] = taipei['tokens'].apply(lemma_wordnet)
telaviv['tokens'] = telaviv['tokens'].apply(lemma_wordnet)
tallinn['tokens'] = tallinn['tokens'].apply(lemma_wordnet)
all_public['tokens'] = all_public['tokens'].apply(lemma_wordnet)
all_corpo['tokens'] = all_corpo['tokens'].apply(lemma_wordnet)
all_startup['tokens'] = all_startup['tokens'].apply(lemma_wordnet)
all_academic['tokens'] = all_academic['tokens'].apply(lemma_wordnet)
all_civil['tokens'] = all_civil['tokens'].apply(lemma_wordnet)
all_media['tokens'] = all_media['tokens'].apply(lemma_wordnet)
all_city['tokens'] = all_city['tokens'].apply(lemma_wordnet)
global_['tokens'] = global_['tokens'].apply(lemma_wordnet)

In [39]:
#create a column with the number of clean token in each tweet
tw_public['num_token'] = tw_public['tokens'].apply(lambda x: len(x))
tw_corpo['num_token'] = tw_corpo['tokens'].apply(lambda x: len(x))
tw_startup['num_token'] = tw_startup['tokens'].apply(lambda x: len(x))
tw_academic['num_token'] = tw_academic['tokens'].apply(lambda x: len(x))
tw_civil['num_token'] = tw_civil['tokens'].apply(lambda x: len(x))
tw_media['num_token'] = tw_media['tokens'].apply(lambda x: len(x))
il_public['num_token'] = il_public['tokens'].apply(lambda x: len(x))
il_corpo['num_token'] = il_corpo['tokens'].apply(lambda x: len(x))
il_startup['num_token'] = il_startup['tokens'].apply(lambda x: len(x))
il_academic['num_token'] = il_academic['tokens'].apply(lambda x: len(x))
il_civil['num_token'] = il_civil['tokens'].apply(lambda x: len(x))
il_media['num_token'] = il_media['tokens'].apply(lambda x: len(x))
ee_public['num_token'] = ee_public['tokens'].apply(lambda x: len(x))
ee_corpo['num_token'] = ee_corpo['tokens'].apply(lambda x: len(x))
ee_startup['num_token'] = ee_startup['tokens'].apply(lambda x: len(x))
ee_academic['num_token'] = ee_academic['tokens'].apply(lambda x: len(x))
ee_civil['num_token'] = ee_civil['tokens'].apply(lambda x: len(x))
ee_media['num_token'] = ee_media['tokens'].apply(lambda x: len(x))
taipei['num_token'] = taipei['tokens'].apply(lambda x: len(x))
telaviv['num_token'] = telaviv['tokens'].apply(lambda x: len(x))
tallinn['num_token'] = tallinn['tokens'].apply(lambda x: len(x))
all_public['num_token'] = all_public['tokens'].apply(lambda x: len(x))
all_corpo['num_token'] = all_corpo['tokens'].apply(lambda x: len(x))
all_startup['num_token'] = all_startup['tokens'].apply(lambda x: len(x))
all_academic['num_token'] = all_academic['tokens'].apply(lambda x: len(x))
all_civil['num_token'] = all_civil['tokens'].apply(lambda x: len(x))
all_media['num_token'] = all_media['tokens'].apply(lambda x: len(x))
all_city['num_token'] = all_city['tokens'].apply(lambda x: len(x))
global_['num_token'] = global_['tokens'].apply(lambda x: len(x))

In [40]:
#calculare means and standard devs for num_token column
#calculate length of clean text mean and standard dev
print('tw_public num of token mean', ("%.2f" % (np.mean(tw_public['num_token']))))
print('tw_corpo num of token mean', ("%.2f" % (np.mean(tw_corpo['num_token']))))
print('tw_startup num of token mean', ("%.2f" % (np.mean(tw_startup['num_token']))))
print('tw_academic num of token mean', ("%.2f" % (np.mean(tw_academic['num_token']))))
print('tw_civil num of token mean', ("%.2f" % (np.mean(tw_civil['num_token']))))
print('tw_media num of token mean', ("%.2f" % (np.mean(tw_media['num_token']))))
print('il_public num of token mean', ("%.2f" % (np.mean(il_public['num_token']))))
print('il_corpo num of token mean', ("%.2f" % (np.mean(il_corpo['num_token']))))
print('il_startup num of token mean', ("%.2f" % (np.mean(il_startup['num_token']))))
print('il_academic num of token mean', ("%.2f" % (np.mean(il_academic['num_token']))))
print('il_civil num of token mean', ("%.2f" % (np.mean(il_civil['num_token']))))
print('il_media num of token mean', ("%.2f" % (np.mean(il_media['num_token']))))
print('ee_public num of token mean', ("%.2f" % (np.mean(ee_public['num_token']))))
print('ee_corpo num of token mean', ("%.2f" % (np.mean(ee_corpo['num_token']))))
print('ee_startup num of token mean', ("%.2f" % (np.mean(ee_startup['num_token']))))
print('ee_academic num of token mean', ("%.2f" % (np.mean(ee_academic['num_token']))))
print('ee_civil num of token mean', ("%.2f" % (np.mean(ee_civil['num_token']))))
print('ee_media num of token mean', ("%.2f" % (np.mean(ee_media['num_token']))))
print('taipei num of token mean', ("%.2f" % (np.mean(taipei['num_token']))))
print('telaviv num of token mean', ("%.2f" % (np.mean(telaviv['num_token']))))
print('tallinn num of token mean', ("%.2f" % (np.mean(tallinn['num_token']))))
print('all_public num of token mean', ("%.2f" % (np.mean(all_public['num_token']))))
print('all_corpo num of token mean', ("%.2f" % (np.mean(all_corpo['num_token']))))
print('all_startup num of token mean', ("%.2f" % (np.mean(all_startup['num_token']))))
print('all_academic num of token mean', ("%.2f" % (np.mean(all_academic['num_token']))))
print('all_civil num of token mean', ("%.2f" % (np.mean(all_civil['num_token']))))
print('all_media num of token mean', ("%.2f" % (np.mean(all_media['num_token']))))
print('all_city num of token mean', ("%.2f" % (np.mean(all_city['num_token']))))
print('global num of token mean', ("%.2f" % (np.mean(global_['num_token']))))

print('tw_public num of token std', ("%.2f" % (np.std(tw_public['num_token']))))
print('tw_corpo num of token std', ("%.2f" % (np.std(tw_corpo['num_token']))))
print('tw_startup num of token std', ("%.2f" % (np.std(tw_startup['num_token']))))
print('tw_academic num of token std', ("%.2f" % (np.std(tw_academic['num_token']))))
print('tw_civil num of token std', ("%.2f" % (np.std(tw_civil['num_token']))))
print('tw_media num of token std', ("%.2f" % (np.std(tw_media['num_token']))))
print('il_public num of token std', ("%.2f" % (np.std(il_public['num_token']))))
print('il_corpo num of token std', ("%.2f" % (np.std(il_corpo['num_token']))))
print('il_startup num of token std', ("%.2f" % (np.std(il_startup['num_token']))))
print('il_academic num of token std', ("%.2f" % (np.std(il_academic['num_token']))))
print('il_civil num of token std', ("%.2f" % (np.std(il_civil['num_token']))))
print('il_media num of token std', ("%.2f" % (np.std(il_media['num_token']))))
print('ee_public num of token std', ("%.2f" % (np.std(ee_public['num_token']))))
print('ee_corpo num of token std', ("%.2f" % (np.std(ee_corpo['num_token']))))
print('ee_startup num of token std', ("%.2f" % (np.std(ee_startup['num_token']))))
print('ee_academic num of token std', ("%.2f" % (np.std(ee_academic['num_token']))))
print('ee_civil num of token std', ("%.2f" % (np.std(ee_civil['num_token']))))
print('ee_media num of token std', ("%.2f" % (np.std(ee_media['num_token']))))
print('taipei num of token std', ("%.2f" % (np.std(taipei['num_token']))))
print('telaviv num of token std', ("%.2f" % (np.std(telaviv['num_token']))))
print('tallinn num of token std', ("%.2f" % (np.std(tallinn['num_token']))))
print('all_public num of token std', ("%.2f" % (np.std(all_public['num_token']))))
print('all_corpo num of token std', ("%.2f" % (np.std(all_corpo['num_token']))))
print('all_startup num of token std', ("%.2f" % (np.std(all_startup['num_token']))))
print('all_academic num of token std', ("%.2f" % (np.std(all_academic['num_token']))))
print('all_civil num of token  std', ("%.2f" % (np.std(all_civil['num_token']))))
print('all_media num of token std', ("%.2f" % (np.std(all_media['num_token']))))
print('all_city num of token std', ("%.2f" % (np.std(all_city['num_token']))))
print('global num of token std', ("%.2f" % (np.std(global_['num_token']))))

tw_public num of token mean 12.97
tw_corpo num of token mean 11.75
tw_startup num of token mean 9.14
tw_academic num of token mean 13.25
tw_civil num of token mean 12.96
tw_media num of token mean 8.48
il_public num of token mean 17.72
il_corpo num of token mean 16.59
il_startup num of token mean 11.32
il_academic num of token mean 11.81
il_civil num of token mean 12.70
il_media num of token mean 13.14
ee_public num of token mean 10.00
ee_corpo num of token mean 13.55
ee_startup num of token mean 15.55
ee_academic num of token mean 11.20
ee_civil num of token mean 14.81
ee_media num of token mean 6.83
taipei num of token mean 12.38
telaviv num of token mean 11.68
tallinn num of token mean 11.78
all_public num of token mean 11.71
all_corpo num of token mean 14.05
all_startup num of token mean 11.58
all_academic num of token mean 11.85
all_civil num of token mean 13.07
all_media num of token mean 9.34
all_city num of token mean 11.99
global num of token mean 11.92
tw_public num of token 

In [41]:
#concatenate the clean_tokens of each dataset in a single list
tw_public_tok_list = tw_public['tokens'].tolist()
tw_corpo_tok_list = tw_corpo['tokens'].tolist()
tw_startup_tok_list = tw_startup['tokens'].tolist()
tw_academic_tok_list = tw_academic['tokens'].tolist()
tw_civil_tok_list = tw_civil['tokens'].tolist()
tw_media_tok_list = tw_media['tokens'].tolist()
il_public_tok_list = il_public['tokens'].tolist()
il_corpo_tok_list = il_corpo['tokens'].tolist()
il_startup_tok_list = il_startup['tokens'].tolist()
il_academic_tok_list = il_academic['tokens'].tolist()
il_civil_tok_list = il_civil['tokens'].tolist()
il_media_tok_list = il_media['tokens'].tolist()
ee_public_tok_list = ee_public['tokens'].tolist()
ee_corpo_tok_list = ee_corpo['tokens'].tolist()
ee_startup_tok_list = ee_startup['tokens'].tolist()
ee_academic_tok_list = ee_academic['tokens'].tolist()
ee_civil_tok_list = ee_civil['tokens'].tolist()
ee_media_tok_list = ee_media['tokens'].tolist()
taipei_tok_list = taipei['tokens'].tolist()
telaviv_tok_list = telaviv['tokens'].tolist()
tallinn_tok_list = tallinn['tokens'].tolist()
all_public_tok_list = all_public['tokens'].tolist()
all_corpo_tok_list = all_corpo['tokens'].tolist()
all_startup_tok_list = all_startup['tokens'].tolist()
all_academic_tok_list = all_academic['tokens'].tolist()
all_civil_tok_list = all_civil['tokens'].tolist()
all_media_tok_list = all_media['tokens'].tolist()
all_city_tok_list = all_city['tokens'].tolist()
global_tok_list = global_['tokens'].tolist()

In [42]:
#how many clean tokens are there in each dataset ?
print('There are', len(tw_public_tok_list), 'clean tokens in Ko-P tweets') 
print('There are', len(tw_corpo_tok_list), 'clean tokens in Asus tweets') 
print('There are', len(tw_startup_tok_list), 'clean tokens in Gogoro tweets') 
print('There are', len(tw_academic_tok_list), 'clean tokens in Academia Sinica tweets') 
print('There are', len(tw_civil_tok_list), 'clean tokens in g0v tweets') 
print('There are', len(tw_media_tok_list), 'clean tokens in Taiwan News tweets') 
print('There are', len(il_public_tok_list), 'clean tokens in Ron Huldai tweets') 
print('There are', len(il_corpo_tok_list), 'clean tokens in Check Point Software tweets') 
print('There are', len(il_startup_tok_list), 'clean tokens in Moovit tweets') 
print('There are', len(il_academic_tok_list), 'clean tokens in Tel Aviv University tweets') 
print('There are', len(il_civil_tok_list), 'clean tokens in Hasadna tweets') 
print('There are', len(il_media_tok_list), 'clean tokens in Israel Hayom tweets') 
print('There are', len(ee_public_tok_list), 'clean tokens in Startup Estonia tweets') 
print('There are', len(ee_corpo_tok_list), 'clean tokens in Bolt tweets') 
print('There are', len(ee_startup_tok_list), 'clean tokens in AdCash tweets') 
print('There are', len(ee_academic_tok_list), 'clean tokens in Tallinn Tech University tweets') 
print('There are', len(ee_civil_tok_list), 'clean tokens in CleanTech ForEst tweets') 
print('There are', len(ee_media_tok_list), 'clean tokens in Postimees tweets')
print('There are', len(taipei_tok_list), 'clean tokens in #Taipei tweets')
print('There are', len(telaviv_tok_list), 'clean tokens in #Telaviv tweets')
print('There are', len(tallinn_tok_list), 'clean tokens in #Tallinn tweets')
print('There are', len(all_public_tok_list), 'clean tokens in Public Sector category')
print('There are', len(all_corpo_tok_list), 'clean tokens in Corporate Company category')
print('There are', len(all_startup_tok_list), 'clean tokens in Startup category')
print('There are', len(all_academic_tok_list), 'clean tokens in Academic Sector category tweets')
print('There are', len(all_civil_tok_list), 'clean tokens in Civil Society category tweets')
print('There are', len(all_media_tok_list), 'clean tokens in Media category tweets')
print('There are', len(all_city_tok_list), 'clean tokens in Case Study Cities tweets')
print('There are', len(global_tok_list), 'clean tokens in total')

There are 1274 clean tokens in Ko-P tweets
There are 3639 clean tokens in Asus tweets
There are 988 clean tokens in Gogoro tweets
There are 376 clean tokens in Academia Sinica tweets
There are 156 clean tokens in g0v tweets
There are 3223 clean tokens in Taiwan News tweets
There are 707 clean tokens in Ron Huldai tweets
There are 3790 clean tokens in Check Point Software tweets
There are 3658 clean tokens in Moovit tweets
There are 3311 clean tokens in Tel Aviv University tweets
There are 2171 clean tokens in Hasadna tweets
There are 2877 clean tokens in Israel Hayom tweets
There are 3410 clean tokens in Startup Estonia tweets
There are 2540 clean tokens in Bolt tweets
There are 846 clean tokens in AdCash tweets
There are 637 clean tokens in Tallinn Tech University tweets
There are 469 clean tokens in CleanTech ForEst tweets
There are 3229 clean tokens in Postimees tweets
There are 17341 clean tokens in #Taipei tweets
There are 17620 clean tokens in #Telaviv tweets
There are 6299 clean

In [43]:
# join the list of tokens in a string
tw_public_tok_text = [' '.join(x) for x in tw_public_tok_list]
tw_corpo_tok_text = [' '.join(x) for x in tw_corpo_tok_list]
tw_startup_tok_text = [' '.join(x) for x in tw_startup_tok_list]
tw_academic_tok_text = [' '.join(x) for x in tw_academic_tok_list]
tw_civil_tok_text = [' '.join(x) for x in tw_civil_tok_list]
tw_media_tok_text = [' '.join(x) for x in tw_media_tok_list]
il_public_tok_text = [' '.join(x) for x in il_public_tok_list]
il_corpo_tok_text = [' '.join(x) for x in il_corpo_tok_list]
il_startup_tok_text = [' '.join(x) for x in il_startup_tok_list]
il_academic_tok_text = [' '.join(x) for x in il_academic_tok_list]
il_civil_tok_text = [' '.join(x) for x in il_civil_tok_list]
il_media_tok_text = [' '.join(x) for x in il_media_tok_list]
ee_public_tok_text = [' '.join(x) for x in ee_public_tok_list]
ee_corpo_tok_text = [' '.join(x) for x in ee_corpo_tok_list]
ee_startup_tok_text = [' '.join(x) for x in ee_startup_tok_list]
ee_academic_tok_text = [' '.join(x) for x in ee_academic_tok_list]
ee_civil_tok_text = [' '.join(x) for x in ee_civil_tok_list]
ee_media_tok_text = [' '.join(x) for x in ee_media_tok_list]
taipei_tok_text = [' '.join(x) for x in taipei_tok_list]
telaviv_tok_text = [' '.join(x) for x in telaviv_tok_list]
tallinn_tok_text = [' '.join(x) for x in tallinn_tok_list]
all_public_tok_text = [' '.join(x) for x in all_public_tok_list]
all_corpo_tok_text = [' '.join(x) for x in all_corpo_tok_list]
all_startup_tok_text = [' '.join(x) for x in all_startup_tok_list]
all_academic_tok_text = [' '.join(x) for x in all_academic_tok_list]
all_civil_tok_text = [' '.join(x) for x in all_civil_tok_list]
all_media_tok_text = [' '.join(x) for x in all_media_tok_list]
all_city_tok_text = [' '.join(x) for x in all_city_tok_list]
global_tok_text = [' '.join(x) for x in global_tok_list]

## re-process outside of dataframe in order to extract text features

In [44]:
#concatenate all rows of 'content' column in a list
tw_public_list = tw_public['content'].to_list
tw_corpo_list = tw_corpo['content'].to_list
tw_startup_list = tw_startup['content'].to_list
tw_academic_list = tw_academic['content'].to_list
tw_civil_list = tw_civil['content'].to_list
tw_media_list = tw_media['content'].to_list
il_public_list = il_public['content'].to_list
il_corpo_list = il_corpo['content'].to_list
il_startup_list = il_startup['content'].to_list
il_academic_list = il_academic['content'].to_list
il_civil_list = il_civil['content'].to_list
il_media_list = il_media['content'].to_list
ee_public_list = ee_public['content'].to_list
ee_corpo_list = ee_corpo['content'].to_list
ee_startup_list = ee_startup['content'].to_list
ee_academic_list = ee_academic['content'].to_list
ee_civil_list = ee_civil['content'].to_list
ee_media_list = ee_media['content'].to_list
taipei_list = taipei['content'].to_list
telaviv_list = telaviv['content'].to_list
tallinn_list = tallinn['content'].to_list
all_public_list = all_public['content'].to_list
all_corpo_list = all_corpo['content'].to_list
all_startup_list = all_startup['content'].to_list
all_academic_list = all_academic['content'].to_list
all_civil_list = all_civil['content'].to_list
all_media_list = all_media['content'].to_list
all_city_list = all_city['content'].to_list
global_list = global_['content'].to_list

In [45]:
#convert the list into a string

tw_public_string = str(tw_public_list).strip('[]')
tw_corpo_string = str(tw_corpo_list).strip('[]')
tw_startup_string = str(tw_startup_list).strip('[]')
tw_academic_string = str(tw_academic_list).strip('[]')
tw_civil_string = str(tw_civil_list).strip('[]')
tw_media_string = str(tw_media_list).strip('[]')
il_public_string = str(il_public_list).strip('[]')
il_corpo_string = str(il_corpo_list).strip('[]')
il_startup_string = str(il_startup_list).strip('[]')
il_academic_string = str(il_academic_list).strip('[]')
il_civil_string = str(il_civil_list).strip('[]')
il_media_string = str(il_media_list).strip('[]')
ee_public_string = str(ee_public_list).strip('[]')
ee_corpo_string = str(ee_corpo_list).strip('[]')
ee_startup_string = str(ee_startup_list).strip('[]')
ee_academic_string = str(ee_academic_list).strip('[]')
ee_civil_string = str(ee_civil_list).strip('[]')
ee_media_string = str(ee_media_list).strip('[]')
taipei_string = str(taipei_list).strip('[]')
telaviv_string = str(telaviv_list).strip('[]')
tallinn_string = str(tallinn_list).strip('[]')
all_public_string = str(all_public_list).strip('[]')
all_corpo_string = str(all_corpo_list).strip('[]')
all_startup_string = str(all_startup_list).strip('[]')
all_academic_string = str(all_academic_list).strip('[]')
all_civil_string = str(all_civil_list).strip('[]')
all_media_string = str(all_media_list).strip('[]')
all_city_string = str(all_city_list).strip('[]')
global_string = str(global_list).strip('[]')

In [46]:
tw_public_string = tw_public_string.lower()
tw_corpo_string = tw_corpo_string.lower()
tw_startup_string = tw_startup_string.lower()
tw_academic_string = tw_academic_string.lower()
tw_civil_string = tw_civil_string.lower()
tw_media_string = tw_media_string.lower()
il_public_string = il_public_string.lower()
il_corpo_string = il_corpo_string.lower()
il_startup_string = il_startup_string.lower()
il_academic_string = il_academic_string.lower()
il_civil_string = il_civil_string.lower()
il_media_string = il_media_string.lower()
ee_public_string = ee_public_string.lower()
ee_corpo_string = ee_corpo_string.lower()
ee_startup_string = ee_startup_string.lower()
ee_academic_string = ee_academic_string.lower()
ee_civil_string = ee_civil_string.lower()
ee_media_string = ee_media_string.lower()
taipei_string = taipei_string.lower()
telaviv_string = telaviv_string.lower()
tallinn_string = tallinn_string.lower()
all_public_string = all_public_string.lower()
all_corpo_string = all_corpo_string.lower()
all_startup_string = all_startup_string.lower()
all_academic_string = all_academic_string.lower()
all_civil_string = all_civil_string.lower()
all_media_string = all_media_string.lower()
all_city_string = all_city_string.lower()
global_string = global_string.lower()

In [47]:
from nltk.tokenize import word_tokenize

tw_public_string = word_tokenize(tw_public_string)
tw_corpo_string = word_tokenize(tw_corpo_string)
tw_startup_string = word_tokenize(tw_startup_string)
tw_academic_string = word_tokenize(tw_academic_string)
tw_civil_string = word_tokenize(tw_civil_string)
tw_media_string = word_tokenize(tw_media_string)
il_public_string = word_tokenize(il_public_string)
il_corpo_string = word_tokenize(il_corpo_string)
il_startup_string = word_tokenize(il_startup_string)
il_academic_string = word_tokenize(il_academic_string)
il_civil_string = word_tokenize(il_civil_string)
il_media_string = word_tokenize(il_media_string)
ee_public_string = word_tokenize(ee_public_string)
ee_corpo_string = word_tokenize(ee_corpo_string)
ee_startup_string = word_tokenize(ee_startup_string)
ee_academic_string = word_tokenize(ee_academic_string)
ee_civil_string = word_tokenize(ee_civil_string)
ee_media_string = word_tokenize(ee_media_string)
taipei_string = word_tokenize(taipei_string)
telaviv_string = word_tokenize(telaviv_string)
tallinn_string = word_tokenize(tallinn_string)
all_public_string = word_tokenize(all_public_string)
all_corpo_string = word_tokenize(all_corpo_string)
all_startup_string = word_tokenize(all_startup_string)
all_academic_string = word_tokenize(all_academic_string)
all_civil_string = word_tokenize(all_civil_string)
all_media_string = word_tokenize(all_media_string)
all_city_string = word_tokenize(all_city_string)
global_string = word_tokenize(global_string)

In [48]:
a = set(stopwords.words('english'))

tw_public_string = [x for x in tw_public_string if x not in a]
tw_corpo_string = [x for x in tw_corpo_string if x not in a]
tw_startup_string = [x for x in tw_startup_string if x not in a]
tw_academic_string = [x for x in tw_academic_string if x not in a]
tw_civil_string = [x for x in tw_civil_string if x not in a]
tw_media_string = [x for x in tw_media_string if x not in a]
il_public_string = [x for x in il_public_string if x not in a]
il_corpo_string = [x for x in il_corpo_string if x not in a]
il_startup_string = [x for x in il_startup_string if x not in a]
il_academic_string = [x for x in il_academic_string if x not in a]
il_civil_string = [x for x in il_civil_string if x not in a]
il_media_string = [x for x in il_media_string if x not in a]
ee_public_string = [x for x in ee_public_string if x not in a]
ee_corpo_string = [x for x in ee_corpo_string if x not in a]
ee_startup_string = [x for x in ee_startup_string if x not in a]
ee_academic_string = [x for x in ee_academic_string if x not in a]
ee_civil_string = [x for x in ee_civil_string if x not in a]
ee_media_string = [x for x in ee_media_string if x not in a]
taipei_string = [x for x in taipei_string if x not in a]
telaviv_string = [x for x in telaviv_string if x not in a]
tallinn_string = [x for x in tallinn_string if x not in a]
all_public_string = [x for x in all_public_string if x not in a]
all_corpo_string = [x for x in all_corpo_string if x not in a]
all_startup_string = [x for x in all_startup_string if x not in a]
all_academic_string = [x for x in all_academic_string if x not in a]
all_civil_string = [x for x in all_civil_string if x not in a]
all_media_string = [x for x in all_media_string if x not in a]
all_city_string = [x for x in all_city_string if x not in a]
global_string = [x for x in global_string if x not in a]

In [49]:
b = [",", ".", ";", " ", ":", "'", "als", "&", "etc", "(", ")", "/", "[1-9]", "_", "-", "’", "--", "``", "'s", ""]

tw_public_string = [x for x in tw_public_string if x not in b]
tw_corpo_string = [x for x in tw_corpo_string if x not in b]
tw_startup_string = [x for x in tw_startup_string if x not in b]
tw_academic_string = [x for x in tw_academic_string if x not in b]
tw_civil_string = [x for x in tw_civil_string if x not in b]
tw_media_string = [x for x in tw_media_string if x not in b]
il_public_string = [x for x in il_public_string if x not in b]
il_corpo_string = [x for x in il_corpo_string if x not in b]
il_startup_string = [x for x in il_startup_string if x not in b]
il_academic_string = [x for x in il_academic_string if x not in b]
il_civil_string = [x for x in il_civil_string if x not in b]
il_media_string = [x for x in il_media_string if x not in b]
ee_public_string = [x for x in ee_public_string if x not in b]
ee_corpo_string = [x for x in ee_corpo_string if x not in b]
ee_startup_string = [x for x in ee_startup_string if x not in b]
ee_academic_string = [x for x in ee_academic_string if x not in b]
ee_civil_string = [x for x in ee_civil_string if x not in b]
ee_media_string = [x for x in ee_media_string if x not in b]
taipei_string = [x for x in taipei_string if x not in b]
telaviv_string = [x for x in telaviv_string if x not in b]
tallinn_string = [x for x in tallinn_string if x not in b]
all_public_string = [x for x in all_public_string if x not in b]
all_corpo_string = [x for x in all_corpo_string if x not in b]
all_startup_string = [x for x in all_startup_string if x not in b]
all_academic_string = [x for x in all_academic_string if x not in b]
all_civil_string = [x for x in all_civil_string if x not in b]
all_media_string = [x for x in all_media_string if x not in b]
all_city_string = [x for x in all_city_string if x not in b]
global_string = [x for x in global_string if x not in b]

In [50]:
# check the frequency of top 10 words for each
tw_public10 = FreqDist(tw_public_string).most_common(30)

tw_public30 = FreqDist(tw_public_string).most_common(30)
tw_corpo30 = FreqDist(tw_corpo_string).most_common(30)
tw_startup30 = FreqDist(tw_startup_string).most_common(30)
tw_academic30 = FreqDist(tw_academic_string).most_common(30)
tw_civil30 = FreqDist(tw_civil_string).most_common(30)
tw_media30 = FreqDist(tw_media_string).most_common(30)
il_public30 = FreqDist(il_public_string).most_common(30)
il_corpo30 = FreqDist(il_corpo_string).most_common(30)
il_startup30 = FreqDist(il_startup_string).most_common(30)
il_academic30 = FreqDist(il_academic_string).most_common(30)
il_civil30 = FreqDist(il_civil_string).most_common(30)
il_media30 = FreqDist(il_media_string).most_common(30)
ee_public30 = FreqDist(ee_public_string).most_common(30)
ee_corpo30 = FreqDist(ee_corpo_string).most_common(30)
ee_startup30 = FreqDist(ee_startup_string).most_common(30)
ee_academic30 = FreqDist(ee_academic_string).most_common(30)
ee_civil30 = FreqDist(ee_civil_string).most_common(30)
ee_media30 = FreqDist(ee_media_string).most_common(30)
taipei30 = FreqDist(taipei_string).most_common(30)
telaviv30 = FreqDist(telaviv_string).most_common(30)
tallinn30 = FreqDist(tallinn_string).most_common(30)
all_public30 = FreqDist(all_public_string).most_common(30)
all_corpo30 = FreqDist(all_corpo_string).most_common(30)
all_startup30 = FreqDist(all_startup_string).most_common(30)
all_academic30 = FreqDist(all_academic_string).most_common(30)
all_civil30 = FreqDist(all_civil_string).most_common(30)
all_media30 = FreqDist(all_media_string).most_common(30)
all_city30 = FreqDist(all_city_string).most_common(30)
global30 = FreqDist(global_string).most_common(30)

In [51]:
tw_public30

[('...', 11),
 ('#', 5),
 ('mayor', 3),
 ('ko', 3),
 ('@', 2),
 ('showing', 2),
 ('support', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('on-behalf', 1),
 ('entire', 1),
 ('city', 1),
 ('hall', 1),
 ('wish', 1),
 ('1', 1),
 ('exciting', 1),
 ('watch', 1),
 ('taipei', 1),
 ('development', 1),
 ('2', 1),
 ('recently', 1),
 ('attended', 1),
 ('asiapacificmedicalaca', 1),
 ('3', 1),
 ('阿北提醒大家，避免傳染禽流感，早點施打流感疫苗。\\n', 1),
 ('阿北關心您\\n', 1),
 ('對抗流感大家一起來', 1)]

In [52]:
tw_corpo30

[('@', 10),
 ('asus', 9),
 ('...', 7),
 ('!', 4),
 ('#', 3),
 ('still', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('1323', 1),
 ('wow', 1),
 ('intel', 1),
 ('gu', 1),
 ('1324', 1),
 ('gpu', 1),
 ('cpu？', 1),
 ('1325', 1),
 ('battery', 1),
 ('charges', 1),
 ('100', 1),
 ('%', 1),
 ('even', 1),
 ('1326', 1),
 ('want', 1),
 ('buy', 1),
 ('already', 1),
 ('1327', 1),
 ('enjoying', 1),
 ('21daylockdownsa', 1)]

In [53]:
tw_startup30

[('...', 11),
 ('gogoro', 7),
 ("'re", 3),
 ('2', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('240,000', 1),
 ('batteries', 1),
 ('engerg', 1),
 ('1', 1),
 ('app', 1),
 ('lets', 1),
 ('rider', 1),
 ('monitor', 1),
 ('battery', 1),
 ('set', 1),
 ('design', 1),
 ('energy', 1),
 ('net', 1),
 ('3', 1),
 ('takes', 1),
 ('great', 1),
 ('pride', 1),
 ('selected', 1),
 ('4', 1),
 ('dhl', 1),
 ('express', 1)]

In [54]:
tw_academic30

[('...', 11),
 ('@', 4),
 ('academia', 3),
 ('sinica', 3),
 ('#', 3),
 ('1', 2),
 ('3', 2),
 ('2019', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('available', 1),
 ('abrc', 1),
 ('10', 1),
 ('fluorescence-tag', 1),
 ('heard', 1),
 ("'re", 1),
 ('headed', 1),
 ('2', 1),
 ('“', 1),
 ('eco-pavilion', 1),
 ('”', 1),
 ('taipei', 1),
 ('taiw', 1),
 ('music', 1),
 ('ai', 1),
 ('day', 1),
 ('jan', 1)]

In [55]:
tw_civil30

[('...', 11),
 ('@', 7),
 ('g0v', 3),
 ('join', 2),
 ('la', 2),
 ('taipei', 2),
 ('#', 2),
 ('hi', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('164', 1),
 ('come', 1),
 ('civic', 1),
 ('hackers', 1),
 ('around', 1),
 ('world', 1),
 ('g0', 1),
 ('165', 1),
 ('📸', 1),
 ('finaliza', 1),
 ('reunión', 1),
 ('de', 1),
 ('malcarazramos', 1),
 ('ago', 1),
 ('166', 1),
 ('summit', 1),
 ('year', 1),
 ('selling', 1)]

In [56]:
tw_media30

[('...', 10),
 ('taiwan', 4),
 ('reports', 2),
 ('coronavirus', 2),
 ('#', 2),
 ('2', 2),
 ('taiwanese', 2),
 ('@', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('5', 1),
 ('imported', 1),
 ('cases', 1),
 ('fr', 1),
 ('1', 1),
 ('staff', 1),
 ('members', 1),
 ('washin', 1),
 ('winning', 1),
 ('uniform', 1),
 ('invoice', 1),
 ('numbers', 1),
 ('3', 1),
 ('la', 1),
 ('niña', 1),
 ('bring', 1),
 ('colder', 1)]

In [57]:
il_public30

[('...', 10),
 ('@', 3),
 ('העיר', 2),
 ('הממשלה', 2),
 ('החליטה', 2),
 ('להפסיק', 2),
 ('את', 2),
 ('עבודת', 2),
 ('אני', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('תקדים', 1),
 ('היסטורי', 1),
 ('ישיבת', 1),
 ('מועצת', 1),
 ('תל', 1),
 ('אביב-יפו', 1),
 ('הת', 1),
 ('1', 1),
 ('בתום', 1),
 ('משמרת', 1),
 ('ארוכה', 1),
 ('רופאים', 1),
 ('רופאות', 1),
 ('וצוותי', 1),
 ('רפואה', 1),
 ('2', 1)]

In [58]:
il_corpo30

[('...', 11),
 ('#', 5),
 ('incident', 2),
 ('left', 2),
 ('voting', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('learn', 1),
 ('securely', 1),
 ('connect', 1),
 ('remote', 1),
 ('users', 1),
 ('1', 1),
 ('hackers', 1),
 ('change', 1),
 ('heart', 1),
 ('days', 1),
 ('exploitin', 1),
 ('2', 1),
 ('around', 1),
 ('globe', 1),
 ('hundreds', 1),
 ('thousands', 1),
 ('wel', 1),
 ('3', 1),
 ('84', 1),
 ('%', 1)]

In [59]:
il_startup30

[('...', 10),
 ('@', 6),
 ('#', 3),
 ('!', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('essential', 1),
 ('workers', 1),
 ('relying', 1),
 ('publictransit', 1),
 ('du', 1),
 ('1', 1),
 ('thanks', 1),
 ('sharing', 1),
 ('doug_hanks\\n', 1),
 ('\\ntoday', 1),
 ('dat', 1),
 ('2', 1),
 ('rt', 1),
 ('datatfnsw', 1),
 ('impact', 1),
 ('co', 1),
 ('3', 1),
 ('transit', 1),
 ('data', 1),
 ('moovit', 1),
 ('shows', 1)]

In [60]:
il_academic30

[('...', 8),
 ('#', 6),
 ('@', 5),
 ('coronatau', 3),
 ('https', 3),
 ('!', 2),
 ('zuckerman', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('//t.co/uj8bebv1ma', 1),
 ('1', 1),
 ('university', 1),
 ('online', 1),
 ('teaching', 1),
 ('continues', 1),
 ('ear', 1),
 ('2', 1),
 ('telaviv', 1),
 ('chicago', 1),
 ('lacity', 1),
 ('nycgov', 1),
 ('miamidadeco', 1),
 ('3', 1),
 ('//t.co/btpnrzkap4', 1),
 ('4', 1),
 ('nice', 1),
 ('//t.co/ko4datzugx', 1)]

In [61]:
il_civil30

[('...', 8),
 ('שאלון', 3),
 ('rt', 2),
 ('@', 2),
 ('ומעכשיו', 2),
 ('יותר', 2),
 ('קל', 2),
 ('השאלון', 2),
 ('היומי', 2),
 ('מלאו', 2),
 ('מהיר', 2),
 ('חצי', 2),
 ('דקה', 2),
 ('ועזרו', 2),
 ('http', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('250,000', 1),
 ('כבר', 1),
 ('מילאו', 1),
 ('את', 1),
 ('הבריאות', 1),
 ('של', 1),
 ('חוקרי', 1),
 ('מכ', 1),
 ('1', 1),
 ('segal_eran', 1)]

In [62]:
il_media30

[('...', 11),
 ('gt', 4),
 ('#', 3),
 ('breaking', 2),
 ('coronavirus', 2),
 ('israel', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('\\nno', 1),
 ('confirmed', 1),
 ('case', 1),
 ('1', 1),
 ("'re", 1),
 ('fighting', 1),
 ('tough', 1),
 ('biological', 1),
 ('war', 1),
 ('covid1', 1),
 ('2', 1),
 ('\\nisrael', 1),
 ('death', 1),
 ('toll', 1),
 ('u', 1),
 ('3', 1),
 ('criticized', 1),
 ('vili', 1),
 ('4', 1)]

In [63]:
ee_public30

[('...', 9),
 ('@', 4),
 ('!', 3),
 ('startup', 2),
 ('veriff', 2),
 ('rt', 2),
 ('bonjour', 2),
 ('paris', 2),
 ('\\nthe', 2),
 ('city', 2),
 ('daily', 2),
 ('news', 2),
 ('baltic', 2),
 ('startups', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('estonian', 1),
 ('woola', 1),
 ('first', 1),
 ('place', 1),
 ('1', 1),
 ('way', 1),
 ('bounce', 1),
 ('back', 1),
 ('crisis', 1),
 ('🔥🎉', 1),
 ('2', 1)]

In [64]:
ee_corpo30

[('...', 11),
 ('@', 6),
 ('whyhate123', 3),
 ('us', 3),
 ('hello', 3),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('already', 1),
 ('message', 1),
 ('1', 1),
 ('danoisyboi', 1),
 ('thank', 1),
 ('getting', 1),
 ('2', 1),
 ('please', 1),
 ('forward', 1),
 ('in-app', 1),
 ('messag', 1),
 ('3', 1),
 ('blowshihm', 1),
 ('may', 1),
 ('contact', 1),
 ('saudi', 1),
 ('arabia', 1),
 ('suppor', 1),
 ('4', 1),
 ('aysha', 1)]

In [65]:
ee_startup30

[('...', 11),
 ('adconf', 3),
 ('2', 2),
 ('new', 2),
 ('second', 2),
 ('nouvelle', 2),
 ('exclusivité', 2),
 ('settlers', 2),
 ('online', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('#', 1),
 ('succeed', 1),
 ('affi', 1),
 ('1', 1),
 ('pronksmuna', 1),
 ('2020', 1),
 ("''", 1),
 ('joins', 1),
 ('family', 1),
 ('sports', 1),
 ('indeed', 1),
 ('back', 1),
 ('!', 1),
 ('⚽', 1),
 ('🤼', 1),
 ('ne', 1)]

In [66]:
ee_academic30

[('...', 11),
 ('#', 2),
 ('tut', 2),
 ('new', 2),
 ('rector', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('esmakordselt', 1),
 ('tuli', 1),
 ('kokku', 1),
 ('majanduse', 1),
 ('ergutamise', 1),
 ('e', 1),
 ('1', 1),
 ('check', 1),
 ('birth', 1),
 ('story', 1),
 ('iseauto.👇', 1),
 ('good', 1),
 ('c', 1),
 ('2', 1),
 ('taltech', 1),
 ('macroeconomics', 1),
 ('professor', 1),
 ('karsten', 1),
 ('stae', 1),
 ('3', 1)]

In [67]:
ee_civil30

[('...', 11),
 ('@', 4),
 ("'re", 2),
 ('thrilled', 2),
 ('announce', 2),
 ('https', 2),
 ('breeze', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('rt', 1),
 ('newenergynexus', 1),
 ('1', 1),
 ('partners', 1),
 ('ou', 1),
 ('2', 1),
 ('wef', 1),
 ('👉', 1),
 ('//t.co/yfry0axlsx', 1),
 ('//t', 1),
 ('3', 1),
 ('innoenergyeu', 1),
 ('crowned', 1),
 ('woola', 1),
 ('winner', 1),
 ('4', 1),
 ('30.06', 1),
 ('apply', 1)]

In [68]:
ee_media30

[('...', 11),
 ('punase', 2),
 ('risti', 2),
 ('teenetemärgi', 2),
 ('saaja', 2),
 ('see', 2),
 ('kõigi', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('eesti', 1),
 ('rahva', 1),
 ('muuseumil', 1),
 ('raskused', 1),
 ('omatulu', 1),
 ('mii', 1),
 ('1', 1),
 ('eestit', 1),
 ('laastanud', 1),
 ('tormituuled', 1),
 ('tekitasid', 1),
 ('ühe', 1),
 ('päe', 1),
 ('2', 1),
 ('inimesed', 1),
 ('tänavu', 1),
 ('investeerimiskelmidele', 1),
 ('kaot', 1)]

In [69]:
taipei30

[('...', 11),
 ('#', 5),
 ('taiwan', 2),
 ('taipei', 2),
 ('good', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('full', 1),
 ('unique', 1),
 ('stunning', 1),
 ('landscapes', 1),
 ('1', 1),
 ('party', 1),
 ('old', 1),
 ('japanese-style', 1),
 ('building', 1),
 ('near', 1),
 ('2', 1),
 ('city', 1),
 ('taiwan❤️\\n', 1),
 ('czechre', 1),
 ('3', 1),
 ('@', 1),
 ('iingwen', 1),
 ('center', 1),
 ('congratulates', 1),
 ('freshly', 1)]

In [70]:
telaviv30

[('...', 11),
 ('#', 11),
 ('telaviv', 5),
 ('@', 4),
 ('!', 3),
 ('17620', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('simonsoesan', 1),
 ('emgoyaars', 1),
 ('helemaal', 1),
 ('mee', 1),
 ('eens', 1),
 ('1', 1),
 ('first', 1),
 ('signal', 1),
 ('week', 1),
 ('sent', 1),
 ('9', 1),
 ('min', 1),
 ('2', 1),
 ('pervert', 1),
 ('journalist', 1),
 ('gushes', 1),
 ('“', 1),
 ('g', 1),
 ('3', 1)]

In [71]:
tallinn30

[('...', 11),
 ('#', 10),
 ('tallinn', 5),
 ('estonia', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('nothing', 1),
 ('like', 1),
 ('nature', 1),
 ('https', 1),
 ('//', 1),
 ('1', 1),
 ('service', 1),
 ('desk', 1),
 ('specialist', 1),
 ('2', 1),
 ('popped', 1),
 ('embassy', 1),
 ('today', 1),
 ('first', 1),
 ('3', 1),
 ('missed', 1),
 ('day', 1),
 ('start', 1),
 ('day20', 1),
 ('4', 1),
 ('beautiful', 1)]

In [72]:
all_public30

[('...', 10),
 ('#', 3),
 ('@', 2),
 ('daily', 2),
 ('news', 2),
 ('baltic', 2),
 ('startups', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('on-behalf', 1),
 ('entire', 1),
 ('city', 1),
 ('hall', 1),
 ('wish', 1),
 ('1', 1),
 ('exciting', 1),
 ('watch', 1),
 ('taipei', 1),
 ('development', 1),
 ('2', 1),
 ('recently', 1),
 ('attended', 1),
 ('asiapacificmedicalaca', 1),
 ('3', 1),
 ('阿北提醒大家，避免傳染禽流感，早點施打流感疫苗。\\n', 1),
 ('阿北關心您\\n', 1),
 ('對抗流感大家一起來', 1)]

In [73]:
all_corpo30

[('...', 9),
 ('@', 6),
 ('asus', 5),
 ('!', 4),
 ('still', 2),
 ('#', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('1323', 1),
 ('wow', 1),
 ('intel', 1),
 ('gu', 1),
 ('1324', 1),
 ('gpu', 1),
 ('cpu？', 1),
 ('1325', 1),
 ('battery', 1),
 ('charges', 1),
 ('100', 1),
 ('%', 1),
 ('even', 1),
 ('1326', 1),
 ('want', 1),
 ('buy', 1),
 ('already', 1),
 ('1327', 1),
 ('enjoying', 1),
 ('21daylockdownsa', 1)]

In [74]:
all_startup30

[('...', 11),
 ('gogoro', 6),
 ('2', 2),
 ('nouvelle', 2),
 ('exclusivité', 2),
 ('settlers', 2),
 ('online', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('240,000', 1),
 ('batteries', 1),
 ('engerg', 1),
 ('1', 1),
 ('app', 1),
 ('lets', 1),
 ('rider', 1),
 ('monitor', 1),
 ('battery', 1),
 ('set', 1),
 ('design', 1),
 ('energy', 1),
 ('net', 1),
 ('3', 1),
 ('takes', 1),
 ('great', 1),
 ('pride', 1),
 ('selected', 1)]

In [75]:
all_academic30

[('...', 11),
 ('academia', 3),
 ('sinica', 3),
 ('1', 2),
 ('3', 2),
 ('2019', 2),
 ('tut', 2),
 ('new', 2),
 ('rector', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('available', 1),
 ('abrc', 1),
 ('10', 1),
 ('fluorescence-tag', 1),
 ('heard', 1),
 ("'re", 1),
 ('headed', 1),
 ('2', 1),
 ('“', 1),
 ('eco-pavilion', 1),
 ('”', 1),
 ('taipei', 1),
 ('taiw', 1),
 ('music', 1),
 ('ai', 1),
 ('day', 1)]

In [76]:
all_civil30

[('...', 11),
 ('@', 5),
 ('join', 2),
 ('la', 2),
 ('g0v', 2),
 ('breeze', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('164', 1),
 ('come', 1),
 ('civic', 1),
 ('hackers', 1),
 ('around', 1),
 ('world', 1),
 ('g0', 1),
 ('165', 1),
 ('📸', 1),
 ('finaliza', 1),
 ('reunión', 1),
 ('de', 1),
 ('malcarazramos', 1),
 ('ago', 1),
 ('166', 1),
 ('summit', 1),
 ('year', 1),
 ('selling', 1),
 ('ticket', 1),
 ('167', 1)]

In [77]:
all_media30

[('...', 11),
 ('taiwan', 4),
 ('reports', 2),
 ('coronavirus', 2),
 ('#', 2),
 ('2', 2),
 ('punase', 2),
 ('risti', 2),
 ('teenetemärgi', 2),
 ('saaja', 2),
 ('see', 2),
 ('kõigi', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('5', 1),
 ('imported', 1),
 ('cases', 1),
 ('fr', 1),
 ('1', 1),
 ('staff', 1),
 ('members', 1),
 ('washin', 1),
 ('winning', 1),
 ('uniform', 1),
 ('invoice', 1),
 ('numbers', 1),
 ('3', 1)]

In [78]:
all_city30

[('...', 11),
 ('#', 8),
 ('taiwan', 2),
 ('tallinn', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('full', 1),
 ('unique', 1),
 ('stunning', 1),
 ('landscapes', 1),
 ('1', 1),
 ('party', 1),
 ('old', 1),
 ('japanese-style', 1),
 ('building', 1),
 ('near', 1),
 ('2', 1),
 ('city', 1),
 ('taipei', 1),
 ('taiwan❤️\\n', 1),
 ('czechre', 1),
 ('3', 1),
 ('@', 1),
 ('iingwen', 1),
 ('center', 1),
 ('congratulates', 1),
 ('freshly', 1)]

In [79]:
global30

[('...', 11),
 ('#', 7),
 ('meet', 2),
 ('tallinn', 2),
 ('<', 1),
 ('bound', 1),
 ('method', 1),
 ('indexopsmixin.tolist', 1),
 ('0', 1),
 ('on-behalf', 1),
 ('entire', 1),
 ('city', 1),
 ('hall', 1),
 ('wish', 1),
 ('1', 1),
 ('exciting', 1),
 ('watch', 1),
 ('taipei', 1),
 ('development', 1),
 ('2', 1),
 ('recently', 1),
 ('attended', 1),
 ('asiapacificmedicalaca', 1),
 ('3', 1),
 ('阿北提醒大家，避免傳染禽流感，早點施打流感疫苗。\\n', 1),
 ('阿北關心您\\n', 1),
 ('對抗流感大家一起來', 1),
 ('h', 1),
 ('4', 1),
 ('great', 1)]

In [80]:
# split datasets into test(1/3) and train(2/3) for further ML
test = tw_public_tok_list+tw_corpo_tok_list+tw_startup_tok_list+tw_academic_tok_list+tw_civil_tok_list+tw_media_tok_list+il_public_tok_list+il_corpo_tok_list+il_startup_tok_list+il_academic_tok_list+il_civil_tok_list+il_media_tok_list+ee_public_tok_list+ee_corpo_tok_list+ee_startup_tok_list+ee_academic_tok_list+ee_civil_tok_list+ee_media_tok_list
train = global_tok_list

print(len(test))
print(len(train))

37301
78561


# Some Visualizations

In [81]:
#we need cuflinks to link plotly to pandas
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

In [82]:
#plot the distribution of sentiment polarity
tw_public['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Ko-P Sentiment Polarity Distribution')
tw_corpo['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Asus Sentiment Polarity Distribution')
tw_startup['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Gogoro Sentiment Polarity Distribution')
tw_academic['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Academia Sinica Sentiment Polarity Distribution')
tw_civil['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'g0v Sentiment Polarity Distribution')
tw_media['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Taiwan News Sentiment Polarity Distribution')
il_public['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Ron Huldai Sentiment Polarity Distribution')
il_corpo['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Check Point Software Sentiment Polarity Distribution')
il_startup['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Moovit Sentiment Polarity Distribution')
il_academic['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Tel Aviv University Sentiment Polarity Distribution')
il_civil['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Hasadna Sentiment Polarity Distribution')
il_media['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Israel Hayom Sentiment Polarity Distribution')
ee_public['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Startup Estonia Sentiment Polarity Distribution')
ee_corpo['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Bolt Sentiment Polarity Distribution')
ee_startup['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'AdCash Sentiment Polarity Distribution')
ee_academic['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Tallinn Tech University Sentiment Polarity Distribution')
ee_civil['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'CleanTech ForEst Sentiment Polarity Distribution')
ee_media['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Postimees Sentiment Polarity Distribution')
taipei['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = '#Taipei Sentiment Polarity Distribution')
telaviv['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = '#Telaviv Sentiment Polarity Distribution')
tallinn['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = '#Tallinn Sentiment Polarity Distribution')
all_public['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Public Sector category Sentiment Polarity Distribution')
all_corpo['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Corporate Company category Sentiment Polarity Distribution')
all_startup['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Startup category has Sentiment Polarity Distribution')
all_academic['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Academic Sector category Sentiment Polarity Distribution')
all_civil['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Civil Society category Sentiment Polarity Distribution')
all_media['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Media category Sentiment Polarity Distribution')
all_city['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Case Study Cities Sentiment Polarity Distribution')
global_['polarity'].iplot(kind = "hist", colors = 'red', bins = 50, xTitle = 'Polarity', yTitle = 'Count', title = 'Global Sentiment Polarity Distribution')

In [83]:
#create a wordcloud
import matplotlib.pyplot as plt
%matplotlib inline

def plot_cloud(wordcloud):
    # Set figure size
    plt.figure(figsize=(40, 30))
    # Display image
    plt.imshow(wordcloud) 
    # No axis details
    plt.axis("off");

In [86]:
from wordcloud import WordCloud

# Generate wordcloud
wordcloud = WordCloud(width = 3000, height = 2000, random_state=1, background_color='black', colormap='Set2', collocations=False).generate(global30)
# Plot
plot_cloud(wordcloud)

TypeError: expected string or bytes-like object

In [ ]:
#save image
wordcloud.to_file("wordcloud.png")

In [ ]:
#create another wordcloud with a shape
from PIL import Image

# Import image to np.array
mask = np.array(Image.open('comment.png'))
# Generate wordcloud
wordcloud = WordCloud(width = 3000, height = 2000, random_state=1, background_color='white', colormap='Set2', collocations=False, mask=mask).generate(text)
# Plot
plot_cloud(wordcloud)